Wiktor Pilarczyk nr indeksu: 308533
Ustawianie precyzji obliczeń

In [186]:
setprecision(64)

64

# Obliczanie pochodnej wielomianu

Na podstawie pierwszego algorytmu możemy zauważyć, że 

$$P'_{k}(x) = a_{k}P_{k-1}(x) + (a_{k}x - b_{k})P'_{k-1}(x) - c_{k}P'_{k-2}(x)$$

Na podstawiej powyższego wzoru funckja Clen1(a,b,c,w,x) oblicza pochodną w punkcie x.

In [187]:
function Clen1(a,b,c,w,x)
    n = length(w)
    wyn = Pdy = BigFloat(0)
    Py = BigFloat(a[1])
    Px = (BigFloat(a[2]) * BigFloat(x) - BigFloat(b[2])) * BigFloat(Py)
    Pdx = BigFloat(a[2]) * BigFloat(Py)
    for k in 2:n-1
        P = (BigFloat(a[k+1]) * BigFloat(x) - BigFloat(b[k+1])) * BigFloat(Px) - BigFloat(c[k+1]) * BigFloat(Py)
        Pd = BigFloat(a[k+1]) * BigFloat(Px) + (BigFloat(a[k+1]) * BigFloat(x) - BigFloat(b[k+1])) * BigFloat(Pdx) - BigFloat(c[k+1]) * BigFloat(Pdy)
        wyn += BigFloat(w[k]) * BigFloat(Pdx)
        Py = BigFloat(Px)
        Pdy = BigFloat(Pdx)
        Px = BigFloat(P)
        Pdx = BigFloat(Pd)
    end
    return BigFloat(wyn) + BigFloat(w[n]) * BigFloat(Pdx)
end

Clen1 (generic function with 1 method)

Podobnie dla drugiego algorytmu:

$$B'_{k}(x) = a_{k+1}B_{k+1}(x) + (a_{k+1}x - b_{k+1})B'_{k+1}(x) - c_{k+2}B'_{k+2}(x)$$

Funkcja Clen2(a,b,c,w,x) oblicza pochodną wielomianu w punkcie x.

In [188]:
function Clen2(a,b,c,w,x)
    n = length(w)
    Bdy = BigFloat(0)
    By = BigFloat(w[n])
    Bx = BigFloat(w[n-1]) + (BigFloat(a[n]) * BigFloat(x) - BigFloat(b[n])) * BigFloat(By)
    Bdx = BigFloat(a[n]) * BigFloat(By)
    for k in n-2:-1:1
        B = BigFloat(w[k]) + (BigFloat(a[k+1]) * BigFloat(x) + BigFloat(b[k+1])) * BigFloat(Bx) - BigFloat(c[k+2]) * BigFloat(By)
        Bd = BigFloat(a[k+1]) * BigFloat(Bx) + (BigFloat(a[k+1]) * BigFloat(x) + BigFloat(b[k+1])) * BigFloat(Bdx) - BigFloat(c[k+2]) * BigFloat(Bdy)
        By = BigFloat(Bx)
        Bdy = BigFloat(Bdx)
        Bx = BigFloat(B)
        Bdx = BigFloat(Bd)
    end
    return BigFloat(a[1])*BigFloat(Bdx)
end

Clen2 (generic function with 1 method)

# Przykłady:
## Wielomiany Czebyszewa
Korzystając z postaci trygonometrycznej dla wielomianów Czebyszewa wyliczamy wzór na pochodna wielomianu:

$$T'_{k}(x) = -\frac{k \sin{(k \arccos{x})}}{\sqrt{1 - x^2}} \space dla \space |x| < 1 $$
$$T'_{k}(x) = \frac{k \sinh{(k \space arccosh\space x)}}{\sqrt{x^2 - 1}} \space dla \space x > 1 $$
$$T'_{k}(x) = \frac{(-1)^{k+1}k \sinh{(k \space arccosh\space (-x))}}{\sqrt{x^2 - 1}} \space dla \space x < -1 $$

Funkcja Czeb(k,x) oblicza pochodną k-tego wielomianu Czebyszewa w punkcie x (pomijamy x = 1, aby nie dzielić przez 0).

In [189]:
function Czeb(k,x)
    if x == 1 
        return NAN
    end
    if(x > 1)
        pierw = BigFloat(sqrt(BigFloat(x) * BigFloat(x) - 1))
        return (BigFloat(k) * BigFloat(sinh(BigFloat(k) * BigFloat(acosh(BigFloat(x)))))) / BigFloat(pierw)
    end
    if(x < -1)
        pierw = BigFloat(sqrt(BigFloat(x) * BigFloat(x) - 1))
        if k % 2 == 0
            pierw *= -1
        end
        return (BigFloat(k) * BigFloat(sinh(BigFloat(k) * BigFloat(acosh(BigFloat(-x)))))) / BigFloat(pierw)
    end
    pierw = BigFloat(1 - sqrt(BigFloat(x) * BigFloat(x)))
    return (BigFloat(k) * BigFloat(sin(BigFloat(k) * BigFloat(acos(BigFloat(x)))))) / BigFloat(pierw)
    
end

Czeb (generic function with 1 method)

Funckja blad porównuje wyniki dla liczenia pochodnej wielomianu Czebyszewa za pomocą funkcji Clen1, Clen2 oraz Czeb, gdzie Czeb będzie punktem odniesienia. Pochodna nie będzie liczona w pobliżu 1, aby nie nastąpiło dzielenie przez 0.
Dla podanych poniżej współczynników $a_{k},b_{k}$ i $c_{k}$ poniżej $P_{k}$ jest $T_{k}$-tym wielomianem Czebyszewa.

In [190]:
a = [1,1,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2,2]
b = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
c = [0,0,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1]
start = 2
iter = 100
finish = 100000
function blad(k,w)
    licz = 0
    sum1 = 0
    sum2 = 0
    print("Wyniki dla ")
    print(k)
    println(". wielomianu Czebyszwa:")
    for i in start:iter:finish
        wynclen1 = Clen1(a,b,c,w,i)
        wynclen2 = Clen2(a,b,c,w,i)
        wynczeb = Czeb(k,i)
        print("x: ")
        print(i)
        print(" Czeb: ")
        println(wynczeb)
        print("Clen1: ")
        print(wynclen1)
        print(" BladClen1: ")
        print(wynclen1 - wynczeb)
        if(wynczeb != 0)
            licz += 1
            sum1 += abs((wynclen1 - wynczeb)/wynczeb)
            print(" BladWzgl: ")
            print(abs((wynclen1 - wynczeb)/wynczeb))
        end
        println()
        print("Clen2: ")
        print(wynclen2)
        print(" BladClen2: ")
        print(wynclen2 - wynczeb)
        if(wynczeb != 0)
            sum2 += abs((wynclen2 - wynczeb)/wynczeb)
            print(" BladWzgl: ")
            print(abs((wynclen2 - wynczeb)/wynczeb))
        end
        println()
    end
    print("Sredni błąd względny dla Clen1 wynosił: ")
    println(sum1/licz)
    print("Sredni błąd względny dla Clen2 wynosił: ")
    print(sum2/licz)
end

blad (generic function with 1 method)

In [191]:
w2 = [0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
blad(2,w2)

Wyniki dla 2. wielomianu Czebyszwa:
x: 2 Czeb: 7.99999999999999999957
Clen1: 8.0 BladClen1: 4.33680868994201773603e-19 BladWzgl: 5.42101086242752217063e-20
Clen2: 8.0 BladClen2: 4.33680868994201773603e-19 BladWzgl: 5.42101086242752217063e-20
x: 102 Czeb: 408.0
Clen1: 408.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 408.0 BladClen2: 0.0 BladWzgl: 0.0
x: 202 Czeb: 808.000000000000000333
Clen1: 808.0 BladClen1: -3.33066907387546962127e-16 BladWzgl: 4.12211519043993764842e-19
Clen2: 808.0 BladClen2: -3.33066907387546962127e-16 BladWzgl: 4.12211519043993764842e-19
x: 302 Czeb: 1208.00000000000000033
Clen1: 1208.0 BladClen1: -3.33066907387546962127e-16 BladWzgl: 2.75717638565850134137e-19
Clen2: 1208.0 BladClen2: -3.33066907387546962127e-16 BladWzgl: 2.75717638565850134137e-19
x: 402 Czeb: 1608.0
Clen1: 1608.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 1608.0 BladClen2: 0.0 BladWzgl: 0.0
x: 502 Czeb: 2007.99999999999999989
Clen1: 2008.0 BladClen1: 1.11022302462515654042e-16 BladWzgl: 5.5289991266193054806

Clen2: 19208.0 BladClen2: 3.55271367880050092936e-15 BladWzgl: 1.8496010406083407591e-19
x: 4902 Czeb: 19607.9999999999999964
Clen1: 19608.0 BladClen1: 3.55271367880050092936e-15 BladWzgl: 1.81186948123240561504e-19
Clen2: 19608.0 BladClen2: 3.55271367880050092936e-15 BladWzgl: 1.81186948123240561504e-19
x: 5002 Czeb: 20008.0000000000000053
Clen1: 20008.0 BladClen1: -5.32907051820075139403e-15 BladWzgl: 2.66346987115191493038e-19
Clen2: 20008.0 BladClen2: -5.32907051820075139403e-15 BladWzgl: 2.66346987115191493038e-19
x: 5102 Czeb: 20408.0000000000000124
Clen1: 20408.0 BladClen1: -1.24344978758017532527e-14 BladWzgl: 6.09295270276448120606e-19
Clen2: 20408.0 BladClen2: -1.24344978758017532527e-14 BladWzgl: 6.09295270276448120606e-19
x: 5202 Czeb: 20808.0000000000000107
Clen1: 20808.0 BladClen1: -1.06581410364015027881e-14 BladWzgl: 5.12213621511029545506e-19
Clen2: 20808.0 BladClen2: -1.06581410364015027881e-14 BladWzgl: 5.12213621511029545506e-19
x: 5302 Czeb: 21207.9999999999999947


Clen2: 38408.0 BladClen2: -2.84217094304040074348e-14 BladWzgl: 7.39994517558946245942e-19
x: 9702 Czeb: 38808.0
Clen1: 38808.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 38808.0 BladClen2: 0.0 BladWzgl: 0.0
x: 9802 Czeb: 39208.0
Clen1: 39208.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 39208.0 BladClen2: 0.0 BladWzgl: 0.0
x: 9902 Czeb: 39608.0000000000000213
Clen1: 39608.0 BladClen1: -2.13162820728030055761e-14 BladWzgl: 5.38181227853034880932e-19
Clen2: 39608.0 BladClen2: -2.13162820728030055761e-14 BladWzgl: 5.38181227853034880932e-19
x: 10002 Czeb: 40008.000000000000032
Clen1: 40008.0 BladClen1: -3.19744231092045083642e-14 BladWzgl: 7.99200737582596189224e-19
Clen2: 40008.0 BladClen2: -3.19744231092045083642e-14 BladWzgl: 7.99200737582596189224e-19
x: 10102 Czeb: 40408.0000000000000071
Clen1: 40408.0 BladClen1: -7.10542735760100185871e-15 BladWzgl: 1.75842094575356411039e-19
Clen2: 40408.0 BladClen2: -7.10542735760100185871e-15 BladWzgl: 1.75842094575356411039e-19
x: 10202 Czeb: 40808.0000000000

Clen1: 58408.0 BladClen1: 1.06581410364015027881e-14 BladWzgl: 1.82477418100285967501e-19
Clen2: 58408.0 BladClen2: 1.06581410364015027881e-14 BladWzgl: 1.82477418100285967501e-19
x: 14702 Czeb: 58808.0000000000000178
Clen1: 58808.0 BladClen1: -1.77635683940025046468e-14 BladWzgl: 3.02060406645396963694e-19
Clen2: 58808.0 BladClen2: -1.77635683940025046468e-14 BladWzgl: 3.02060406645396963694e-19
x: 14802 Czeb: 59207.9999999999999538
Clen1: 59208.0 BladClen1: 4.61852778244065120816e-14 BladWzgl: 7.80051307667992705698e-19
Clen2: 59208.0 BladClen2: 4.61852778244065120816e-14 BladWzgl: 7.80051307667992705698e-19
x: 14902 Czeb: 59607.9999999999999574
Clen1: 59608.0 BladClen1: 4.26325641456060111523e-14 BladWzgl: 7.1521547687568801475e-19
Clen2: 59608.0 BladClen2: 4.26325641456060111523e-14 BladWzgl: 7.1521547687568801475e-19
x: 15002 Czeb: 60007.9999999999999609
Clen1: 60008.0 BladClen1: 3.90798504668055102229e-14 BladWzgl: 6.51244008578947977738e-19
Clen2: 60008.0 BladClen2: 3.9079850466

Clen2: 77208.0 BladClen2: -7.10542735760100185871e-15 BladWzgl: 9.20296777225287775599e-20
x: 19402 Czeb: 77608.0000000000000284
Clen1: 77608.0 BladClen1: -2.84217094304040074348e-14 BladWzgl: 3.66221387362179252448e-19
Clen2: 77608.0 BladClen2: -2.84217094304040074348e-14 BladWzgl: 3.66221387362179252448e-19
x: 19502 Czeb: 78007.9999999999999645
Clen1: 78008.0 BladClen1: 3.55271367880050092936e-14 BladWzgl: 4.55429401958837674451e-19
Clen2: 78008.0 BladClen2: 3.55271367880050092936e-14 BladWzgl: 4.55429401958837674451e-19
x: 19602 Czeb: 78408.0000000000000497
Clen1: 78408.0 BladClen1: -4.9737991503207013011e-14 BladWzgl: 6.34348427497283606005e-19
Clen2: 78408.0 BladClen2: -4.9737991503207013011e-14 BladWzgl: 6.34348427497283606005e-19
x: 19702 Czeb: 78807.9999999999999432
Clen1: 78808.0 BladClen1: 5.68434188608080148697e-14 BladWzgl: 7.2128995610608079014e-19
Clen2: 78808.0 BladClen2: 5.68434188608080148697e-14 BladWzgl: 7.2128995610608079014e-19
x: 19802 Czeb: 79207.9999999999999858

...

Clen1: 307608.0 BladClen1: -8.52651282912120223045e-14 BladWzgl: 2.77187616353319882067e-19
Clen2: 307608.0 BladClen2: -8.52651282912120223045e-14 BladWzgl: 2.77187616353319882067e-19
x: 77002 Czeb: 308008.000000000000057
Clen1: 308008.0 BladClen1: -5.68434188608080148697e-14 BladWzgl: 1.84551761190644447087e-19
Clen2: 308008.0 BladClen2: -5.68434188608080148697e-14 BladWzgl: 1.84551761190644447087e-19
x: 77102 Czeb: 308407.999999999999829
Clen1: 308408.0 BladClen1: 1.70530256582424044609e-13 BladWzgl: 5.52937201961116588081e-19
Clen2: 308408.0 BladClen2: 1.70530256582424044609e-13 BladWzgl: 5.52937201961116588081e-19
x: 77202 Czeb: 308808.000000000000085
Clen1: 308808.0 BladClen1: -8.52651282912120223045e-14 BladWzgl: 2.76110490308580160739e-19
Clen2: 308808.0 BladClen2: -8.52651282912120223045e-14 BladWzgl: 2.76110490308580160739e-19
x: 77302 Czeb: 309208.000000000000199
Clen1: 309208.0 BladClen1: -1.98951966012828052044e-13 BladWzgl: 6.43424381040684755605e-19
Clen2: 309208.0 BladCl

Clen1: 327208.0 BladClen1: 2.55795384873636066914e-13 BladWzgl: 7.81751622434769526132e-19
Clen2: 327208.0 BladClen2: 2.55795384873636066914e-13 BladWzgl: 7.81751622434769526132e-19
x: 81902 Czeb: 327608.000000000000227
Clen1: 327608.0 BladClen1: -2.27373675443232059479e-13 BladWzgl: 6.94041889829406056408e-19
Clen2: 327608.0 BladClen2: -2.27373675443232059479e-13 BladWzgl: 6.94041889829406056408e-19
x: 82002 Czeb: 328007.999999999999744
Clen1: 328008.0 BladClen1: 2.55795384873636066914e-13 BladWzgl: 7.79844957664557166611e-19
Clen2: 328008.0 BladClen2: 2.55795384873636066914e-13 BladWzgl: 7.79844957664557166611e-19
x: 82102 Czeb: 328407.999999999999773
Clen1: 328408.0 BladClen1: 2.27373675443232059479e-13 BladWzgl: 6.92351207775791270729e-19
Clen2: 328408.0 BladClen2: 2.27373675443232059479e-13 BladWzgl: 6.92351207775791270729e-19
x: 82202 Czeb: 328808.000000000000085
Clen1: 328808.0 BladClen1: -8.52651282912120223045e-14 BladWzgl: 2.59315856947556088308e-19
Clen2: 328808.0 BladClen2:

Clen1: 346008.0 BladClen1: 8.52651282912120223045e-14 BladWzgl: 2.46425308926995972134e-19
Clen2: 346008.0 BladClen2: 8.52651282912120223045e-14 BladWzgl: 2.46425308926995972134e-19
x: 86602 Czeb: 346408.000000000000142
Clen1: 346408.0 BladClen1: -1.42108547152020037174e-13 BladWzgl: 4.10234599524318252232e-19
Clen2: 346408.0 BladClen2: -1.42108547152020037174e-13 BladWzgl: 4.10234599524318252232e-19
x: 86702 Czeb: 346808.000000000000085
Clen1: 346808.0 BladClen1: -8.52651282912120223045e-14 BladWzgl: 2.4585686688661167645e-19
Clen2: 346808.0 BladClen2: -8.52651282912120223045e-14 BladWzgl: 2.4585686688661167645e-19
x: 86802 Czeb: 347208.0
Clen1: 347208.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 347208.0 BladClen2: 0.0 BladWzgl: 0.0
x: 86902 Czeb: 347608.000000000000284
Clen1: 347608.0 BladClen1: -2.84217094304040074348e-13 BladWzgl: 8.1763680440047431048e-19
Clen2: 347608.0 BladClen2: -2.84217094304040074348e-13 BladWzgl: 8.1763680440047431048e-19
x: 87002 Czeb: 348008.000000000000171
Clen

x: 91202 Czeb: 364807.999999999999858
Clen1: 364808.0 BladClen1: 1.42108547152020037174e-13 BladWzgl: 3.89543395846637237196e-19
Clen2: 364808.0 BladClen2: 1.42108547152020037174e-13 BladWzgl: 3.89543395846637237196e-19
x: 91302 Czeb: 365207.999999999999687
Clen1: 365208.0 BladClen1: 3.12638803734444081783e-13 BladWzgl: 8.56056832639055228927e-19
Clen2: 365208.0 BladClen2: 3.12638803734444081783e-13 BladWzgl: 8.56056832639055228927e-19
x: 91402 Czeb: 365608.000000000000199
Clen1: 365608.0 BladClen1: -1.98951966012828052044e-13 BladWzgl: 5.44167430725881413815e-19
Clen2: 365608.0 BladClen2: -1.98951966012828052044e-13 BladWzgl: 5.44167430725881413815e-19
x: 91502 Czeb: 366007.999999999999972
Clen1: 366008.0 BladClen1: 2.84217094304040074348e-14 BladWzgl: 7.76532464601976116271e-20
Clen2: 366008.0 BladClen2: 2.84217094304040074348e-14 BladWzgl: 7.76532464601976116271e-20
x: 91602 Czeb: 366408.000000000000199
Clen1: 366408.0 BladClen1: -1.98951966012828052044e-13 BladWzgl: 5.4297931817216

Clen2: 384008.0 BladClen2: 0.0 BladWzgl: 0.0
x: 96102 Czeb: 384408.000000000000227
Clen1: 384408.0 BladClen1: -2.27373675443232059479e-13 BladWzgl: 5.91490487823437751925e-19
Clen2: 384408.0 BladClen2: -2.27373675443232059479e-13 BladWzgl: 5.91490487823437751925e-19
x: 96202 Czeb: 384808.000000000000227
Clen1: 384808.0 BladClen1: -2.27373675443232059479e-13 BladWzgl: 5.90875645629072314892e-19
Clen2: 384808.0 BladClen2: -2.27373675443232059479e-13 BladWzgl: 5.90875645629072314892e-19
x: 96302 Czeb: 385207.999999999999744
Clen1: 385208.0 BladClen1: 2.55795384873636066914e-13 BladWzgl: 6.64044840381394122375e-19
Clen2: 385208.0 BladClen2: 2.55795384873636066914e-13 BladWzgl: 6.64044840381394122375e-19
x: 96402 Czeb: 385607.999999999999829
Clen1: 385608.0 BladClen1: 1.70530256582424044609e-13 BladWzgl: 4.42237340984689230201e-19
Clen2: 385608.0 BladClen2: 1.70530256582424044609e-13 BladWzgl: 4.42237340984689230201e-19
x: 96502 Czeb: 386008.000000000000227
Clen1: 386008.0 BladClen1: -2.273

In [192]:
w20 = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
blad(20,w20)

Wyniki dla 20. wielomianu Czebyszwa:
x: 2 Czeb: 1.58631825968e+12
Clen1: 1.58631825968e+12 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 1.58631825968e+12 BladClen2: 0.0 BladWzgl: 0.0
x: 102 Czeb: 1.52691663519261880092e+45
Clen1: 1.52691663519261880077e+45 BladClen1: -1.54742504910672534362e+26 BladWzgl: 1.01343125973050875142e-19
Clen2: 1.52691663519261880092e+45 BladClen2: 0.0 BladWzgl: 0.0
x: 202 Czeb: 6.64091676404337633894e+50
Clen1: 6.64091676404337629269e+50 BladClen1: -4.62438938963258085666e+33 BladWzgl: 6.96348042588171765828e-18
Clen2: 6.64091676404337629391e+50 BladClen2: -4.50269493201067083412e+33 BladWzgl: 6.78023094099009350948e-18
x: 302 Czeb: 1.38264408901219908693e+54
Clen1: 1.38264408901219908875e+54 BladClen1: 1.82768849420425932524e+36 BladWzgl: 1.32187922309783483672e-18
Clen2: 1.38264408901219908842e+54 BladClen2: 1.49538149525803035702e+36 BladWzgl: 1.08153754617095577553e-18
x: 402 Czeb: 3.16871243793242432679e+56
Clen1: 3.16871243793242433402e+56 BladClen1: 7.23100029

x: 4002 Czeb: 2.90980839798968971655e+75
Clen1: 2.90980839798968970263e+75 BladClen1: -1.39273194753891979448e+58 BladWzgl: 4.7863355831302217655e-18
Clen2: 2.90980839798968970224e+75 BladClen2: -1.43196383338508654925e+58 BladWzgl: 4.92116193758459420993e-18
x: 4102 Czeb: 4.65068860725401948645e+75
Clen1: 4.65068860725401944878e+75 BladClen1: -3.7662610412320084583e+58 BladWzgl: 8.09828685446171432208e-18
Clen2: 4.65068860725401944839e+75 BladClen2: -3.80549292707817521308e+58 BladWzgl: 8.18264400919569051272e-18
x: 4202 Czeb: 7.34961713560583166902e+75
Clen1: 7.3496171356058317161e+75 BladClen1: 4.70782630154001057288e+58 BladWzgl: 6.40553951951123329232e-18
Clen2: 7.34961713560583171767e+75 BladClen2: 4.86475384492467759197e+58 BladWzgl: 6.61905750349494106866e-18
x: 4302 Czeb: 1.14904628421038072893e+76
Clen1: 1.1490462842103807207e+76 BladClen1: -8.23869602769501850253e+58 BladWzgl: 7.17002973762420036658e-18
Clen2: 1.14904628421038072038e+76 BladClen2: -8.55255111446435254073e+58

Clen1: 1.1956480600635090834e+81 BladClen1: 3.70238525397271359485e+63 BladWzgl: 3.09655104845488938228e-18
Clen2: 1.1956480600635090834e+81 BladClen2: 3.70238525397271359485e+63 BladWzgl: 3.09655104845488938228e-18
x: 8002 Czeb: 1.51835133826265909715e+81
Clen1: 1.51835133826265909386e+81 BladClen1: -3.29100911464241208431e+63 BladWzgl: 2.16748853292945924425e-18
Clen2: 1.51835133826265909396e+81 BladClen2: -3.18816507980983670668e+63 BladWzgl: 2.09975451627541364281e-18
x: 8102 Czeb: 1.92243835067071142655e+81
Clen1: 1.92243835067071143354e+81 BladClen1: 6.99339436861512567916e+63 BladWzgl: 3.63777302204527377749e-18
Clen2: 1.92243835067071143354e+81 BladClen2: 6.99339436861512567916e+63 BladWzgl: 3.63777302204527377749e-18
x: 8202 Czeb: 2.42703152967017192512e+81
Clen1: 2.42703152967017191957e+81 BladClen1: -5.55357788095907039227e+63 BladWzgl: 2.28821826707533091586e-18
Clen2: 2.42703152967017191936e+81 BladClen2: -5.75926595062422114754e+63 BladWzgl: 2.37296709178182465363e-18
x: 

Clen2: 1.14519260699863220056e+85 BladClen2: -1.60074683336206923781e+67 BladWzgl: 1.39779703744103994343e-18
x: 12902 Czeb: 1.32765004688795423593e+85
Clen1: 1.32765004688795424048e+85 BladClen1: 4.54949100008167046535e+67 BladWzgl: 3.42672454292137756017e-18
Clen2: 1.32765004688795424022e+85 BladClen2: 4.29674150007713321728e+67 BladWzgl: 3.23635095720352325122e-18
x: 13002 Czeb: 1.53742158474173678359e+85
Clen1: 1.53742158474173677138e+85 BladClen1: -1.2216225833552633657e+68 BladWzgl: 7.9459179933425820837e-18
Clen2: 1.53742158474173677129e+85 BladClen2: -1.23004756668874794063e+68 BladWzgl: 8.00071742777942747761e-18
x: 13102 Czeb: 1.77833759056854027575e+85
Clen1: 1.77833759056854026597e+85 BladClen1: -9.77298066684210692557e+67 BladWzgl: 5.49557109891471923354e-18
Clen2: 1.7783375905685402653e+85 BladClen2: -1.04469793335208729204e+68 BladWzgl: 5.87457600228814814627e-18
x: 13202 Czeb: 2.05472990579305333912e+85
Clen1: 2.05472990579305333912e+85 BladClen1: 0.0 BladWzgl: 0.0
Clen

Clen2: 2.00658949112736656759e+87 BladClen2: -3.45087317339528189372e+69 BladWzgl: 1.71977038086473295365e-18
x: 16902 Czeb: 2.24607242709161402736e+87
Clen1: 2.24607242709161404505e+87 BladClen1: 1.76857250136508197053e+70 BladWzgl: 7.87406710501835687486e-18
Clen2: 2.24607242709161404462e+87 BladClen2: 1.72543658669764094686e+70 BladWzgl: 7.68201668782278719522e-18
x: 17002 Czeb: 2.51246564211723956995e+87
Clen1: 2.5124656421172395527e+87 BladClen1: -1.72543658669764094686e+70 BladWzgl: 6.86750321187925177823e-18
Clen2: 2.51246564211723955378e+87 BladClen2: -1.61759680002903838768e+70 BladWzgl: 6.43828426113679854197e-18
x: 17102 Czeb: 2.80860746913166452547e+87
Clen1: 2.80860746913166453668e+87 BladClen1: 1.12153378135346661546e+70 BladWzgl: 3.99320230284871576285e-18
Clen2: 2.80860746913166453647e+87 BladClen2: 1.09996582401974610362e+70 BladWzgl: 3.91640995087085584423e-18
x: 17202 Czeb: 3.13761628155290768248e+87
Clen1: 3.13761628155290765876e+87 BladClen1: -2.3724753067092563019

...

Clen2: 9.34563769782607608398e+99 BladClen2: 3.31999078261232995518e+82 BladWzgl: 3.55244969894842542765e-18
x: 78102 Czeb: 9.57592778751106117514e+99
Clen1: 9.57592778751106110589e+99 BladClen1: -6.92455220373428819224e+82 BladWzgl: 7.23120762540137276191e-18
Clen2: 9.57592778751106110589e+99 BladClen2: -6.92455220373428819224e+82 BladWzgl: 7.23120762540137276191e-18
x: 78202 Czeb: 9.81158694385399953609e+99
Clen1: 9.81158694385399960439e+99 BladClen1: 6.82969532423107876495e+82 BladWzgl: 6.96084676547580869144e-18
Clen2: 9.81158694385399960534e+99 BladClen2: 6.92455220373428819224e+82 BladWzgl: 7.05752519277408381229e-18
x: 78302 Czeb: 1.00527332363802921511e+100
Clen1: 1.00527332363802922706e+100 BladClen1: 1.19519668174043878387e+83 BladWzgl: 1.1889270844421568017e-17
Clen2: 1.00527332363802922706e+100 BladClen2: 1.19519668174043878387e+83 BladWzgl: 1.1889270844421568017e-17
x: 78402 Czeb: 1.02994871751651792493e+100
Clen1: 1.02994871751651793679e+100 BladClen1: 1.18571099379011784

x: 82002 Czeb: 2.41693162418722338222e+100
Clen1: 2.41693162418722338564e+100 BladClen1: 3.41484766211553938248e+82 BladWzgl: 1.41288550654133613968e-18
Clen2: 2.41693162418722338526e+100 BladClen2: 3.03542014410270167331e+82 BladWzgl: 1.25589822803674323526e-18
x: 82102 Czeb: 2.47355122758169611836e+100
Clen1: 2.4735512275816961508e+100 BladClen1: 3.24410527900976241335e+83 BladWzgl: 1.31151732086074879522e-17
Clen2: 2.47355122758169615061e+100 BladClen2: 3.22513390310912052789e+83 BladWzgl: 1.30384762892589061518e-17
x: 82202 Czeb: 2.5314258610870163376e+100
Clen1: 2.5314258610870163395e+100 BladClen1: 1.89713759006418854582e+82 BladWzgl: 7.49434387641730547279e-19
Clen2: 2.53142586108701633931e+100 BladClen2: 1.70742383105776969124e+82 BladWzgl: 6.74490948877557492523e-19
x: 82302 Czeb: 2.59058176595198461892e+100
Clen1: 2.59058176595198458895e+100 BladClen1: -2.9974773923014179024e+83 BladWzgl: 1.15706727797487899433e-17
Clen2: 2.59058176595198458952e+100 BladClen2: -2.940563264599

x: 89002 Czeb: 1.14602862743732480805e+101
Clen1: 1.14602862743732480789e+101 BladClen1: -1.51771007205135083666e+82 BladWzgl: 1.32432125665582723462e-19
Clen2: 1.14602862743732480805e+101 BladClen2: 0.0 BladWzgl: 0.0
x: 89102 Czeb: 1.17074283523298847096e+101
Clen1: 1.17074283523298847187e+101 BladClen1: 9.10626043230810501993e+82 BladWzgl: 7.7781901868277300896e-19
Clen2: 1.17074283523298847195e+101 BladClen2: 9.86511546833378043826e+82 BladWzgl: 8.42637270239670759691e-19
x: 89202 Czeb: 1.19596138499712391209e+101
Clen1: 1.19596138499712391399e+101 BladClen1: 1.89713759006418854582e+83 BladWzgl: 1.58628665930443134307e-18
Clen2: 1.19596138499712391406e+101 BladClen2: 1.97302309366675608765e+83 BladWzgl: 1.6497381256766085968e-18
x: 89302 Czeb: 1.22169398604893929899e+101
Clen1: 1.22169398604893929937e+101 BladClen1: 3.79427518012837709164e+82 BladWzgl: 3.10574924936757763529e-19
Clen2: 1.2216939860489392996e+101 BladClen2: 6.07084028820540334662e+82 BladWzgl: 4.96919879898812421674e

Clen1: 2.58866660828162643862e+101 BladClen1: -6.52615330982080859762e+83 BladWzgl: 2.52104820641732276443e-18
Clen2: 2.58866660828162643831e+101 BladClen2: -6.82969532423107876495e+83 BladWzgl: 2.63830626252975638142e-18
x: 93002 Czeb: 2.64212516376076460648e+101
Clen1: 2.64212516376076457628e+101 BladClen1: -3.02024304338218816495e+84 BladWzgl: 1.14311126694816220251e-17
Clen2: 2.64212516376076457582e+101 BladClen2: -3.06577434554372869004e+84 BladWzgl: 1.16034410011823499947e-17
x: 93102 Czeb: 2.69662845461019778571e+101
Clen1: 2.69662845461019778662e+101 BladClen1: 9.10626043230810501993e+82 BladWzgl: 3.3769058606275184477e-19
Clen2: 2.69662845461019778662e+101 BladClen2: 9.10626043230810501993e+82 BladWzgl: 3.3769058606275184477e-19
x: 93202 Czeb: 2.75219574282998438351e+101
Clen1: 2.75219574282998436013e+101 BladClen1: -2.33727351095908028845e+84 BladWzgl: 8.49239563373405114832e-18
Clen2: 2.75219574282998436013e+101 BladClen2: -2.33727351095908028845e+84 BladWzgl: 8.492395633734

Clen1: 5.65460389075324622289e+101 BladClen1: -2.48904451816421537212e+84 BladWzgl: 4.40180172873727377653e-18
Clen2: 5.65460389075324622349e+101 BladClen2: -2.42833611528216133865e+84 BladWzgl: 4.29444071096319392838e-18
x: 96902 Czeb: 5.76662867018798227251e+101
Clen1: 5.766628670187982332e+101 BladClen1: 5.94942348244129527969e+84 BladWzgl: 1.03169873121852220936e-17
Clen2: 5.76662867018798233321e+101 BladClen2: 6.07084028820540334662e+84 BladWzgl: 1.05275380736583898915e-17
x: 97002 Czeb: 5.8807538065087017576e+101
Clen1: 5.88075380650870179463e+101 BladClen1: 3.70321257580529604144e+84 BladWzgl: 6.29717328364716400721e-18
Clen2: 5.88075380650870179463e+101 BladClen2: 3.70321257580529604144e+84 BladWzgl: 6.29717328364716400721e-18
x: 97102 Czeb: 5.99701645299542947885e+101
Clen1: 5.997016452995429491e+101 BladClen1: 1.21416805764108066932e+84 BladWzgl: 2.02462018765117772844e-18
Clen2: 5.997016452995429491e+101 BladClen2: 1.21416805764108066932e+84 BladWzgl: 2.02462018765117772844e

In [193]:
w39 = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1]
blad(39,w39)

Wyniki dla 39. wielomianu Czebyszwa:
x: 2 Czeb: 2.27734243043799390028e+23
Clen1: 2.27734243043799390028e+23 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 2.27734243043799390044e+23 BladClen2: 16384.0 BladWzgl: 7.19435065232983794061e-20
x: 102 Czeb: 2.27313292500931272516e+89
Clen1: 2.27313292500931273275e+89 BladClen1: 7.59192098146962016618e+71 BladWzgl: 3.33984911218446104255e-18
Clen2: 2.27313292500931273275e+89 BladClen2: 7.59192098146962016618e+71 BladWzgl: 3.33984911218446104255e-18
x: 202 Czeb: 4.299896762719803295e+100
Clen1: 4.29989676271980325592e+100 BladClen1: -3.90810343553222840439e+83 BladWzgl: 9.088830851511526046e-18
Clen2: 4.29989676271980325554e+100 BladClen2: -3.94604618733351217531e+83 BladWzgl: 9.17707192773979328891e-18
x: 302 Czeb: 1.86390695074638266432e+107
Clen1: 1.86390695074638264809e+107 BladClen1: -1.6232630436415436e+90 BladWzgl: 8.70892746545917622913e-18
Clen2: 1.86390695074638264793e+107 BladClen2: -1.63917738720665677254e+90 BladWzgl: 8.79430910727740344686e

x: 5202 Czeb: 1.75661874359732340282e+154
Clen1: 1.75661874359732336823e+154 BladClen1: -3.45975232764708879901e+137 BladWzgl: 1.96955220946918313233e-17
Clen2: 1.75661874359732336808e+154 BladClen2: -3.47428910213300093683e+137 BladWzgl: 1.97782763892073432199e-17
x: 5302 Czeb: 3.62171096895644726115e+154
Clen1: 3.62171096895644723789e+154 BladClen1: -2.32588391774594204976e+137 BladWzgl: 6.42205835220505657319e-18
Clen2: 3.62171096895644723731e+154 BladClen2: -2.384031015689590601e+137 BladWzgl: 6.58260981101018298724e-18
x: 5402 Czeb: 7.3667908320379033673e+154
Clen1: 7.36679083203790341323e+154 BladClen1: 4.59362073754823554827e+137 BladWzgl: 6.23557915825537939406e-18
Clen2: 7.36679083203790341323e+154 BladClen2: 4.59362073754823554827e+137 BladWzgl: 6.23557915825537939406e-18
x: 5502 Czeb: 1.47906268201485000677e+155
Clen1: 1.47906268201484999712e+155 BladClen1: -9.6524182586456595065e+137 BladWzgl: 6.52603731810518887007e-18
Clen2: 1.47906268201484999724e+155 BladClen2: -9.53612

Clen2: 1.97281662724818035943e+163 BladClen2: 4.30801299943606927931e+146 BladWzgl: 2.18368648151814328633e-17
x: 9102 Czeb: 3.00195362073341389432e+163
Clen1: 3.00195362073341390805e+163 BladClen1: 1.37356936213903658181e+146 BladWzgl: 4.57558488796191604257e-18
Clen2: 3.00195362073341390743e+163 BladClen2: 1.31113439113271673718e+146 BladWzgl: 4.36760375669091985895e-18
x: 9202 Czeb: 4.54704334440263939206e+163
Clen1: 4.54704334440263940642e+163 BladClen1: 1.43600433314535642644e+146 BladWzgl: 3.15810566202994754659e-18
Clen2: 4.54704334440263940642e+163 BladClen2: 1.43600433314535642644e+146 BladWzgl: 3.15810566202994754659e-18
x: 9302 Czeb: 6.8565418714785846045e+163
Clen1: 6.85654187147858453957e+163 BladClen1: -6.49323698465726384127e+146 BladWzgl: 9.47013393394041130147e-18
Clen2: 6.85654187147858454019e+163 BladClen2: -6.43080201365094399665e+146 BladWzgl: 9.37907495380636888527e-18
x: 9402 Czeb: 1.02937538085682219726e+164
Clen1: 1.02937538085682216941e+164 BladClen1: -2.78459

Clen1: 1.71858827824548931502e+169 BladClen1: 2.47140990896158711186e+152 BladWzgl: 1.43804652937855199891e-17
Clen2: 1.71858827824548931469e+169 BladClen2: 2.43867600288262569316e+152 BladWzgl: 1.41899955547949833005e-17
x: 13002 Czeb: 2.30457349759096479335e+169
Clen1: 2.3045734975909647819e+169 BladClen1: -1.1456867127636496545e+152 BladWzgl: 4.9713611388886839813e-18
Clen2: 2.30457349759096478141e+169 BladClen2: -1.19478757188209178255e+152 BladWzgl: 5.18441947341248472353e-18
x: 13102 Czeb: 3.0834224668878605177e+169
Clen1: 3.08342246688786053112e+169 BladClen1: 1.34209014923741816671e+152 BladWzgl: 4.35259898262338239096e-18
Clen2: 3.08342246688786053047e+169 BladClen2: 1.27662233707949532931e+152 BladWzgl: 4.14027708103199788414e-18
x: 13202 Czeb: 4.11636710521193684361e+169
Clen1: 4.11636710521193681447e+169 BladClen1: -2.91331764102756626431e+152 BladWzgl: 7.0773999659526724434e-18
Clen2: 4.11636710521193681447e+169 BladClen2: -2.91331764102756626431e+152 BladWzgl: 7.077399965

Clen1: 3.92574134777873434913e+173 BladClen1: -4.12960484242231990667e+156 BladWzgl: 1.05192993541434809399e-17
Clen2: 3.92574134777873434833e+173 BladClen2: -4.21005169000197548927e+156 BladWzgl: 1.07242207701332890104e-17
x: 16902 Czeb: 4.9187203097432506278e+173
Clen1: 4.91872030974325063075e+173 BladClen1: 2.94971774458737136191e+155 BladWzgl: 5.99692106653110742494e-19
Clen2: 4.91872030974325062994e+173 BladClen2: 2.14524926879081553593e+155 BladWzgl: 4.36139713929535085454e-19
x: 17002 Czeb: 6.15467150742624522305e+173
Clen1: 6.15467150742624523592e+173 BladClen1: 1.28714956127448932156e+156 BladWzgl: 2.09133754696966487117e-18
Clen2: 6.15467150742624523968e+173 BladClen2: 1.66256818331288204035e+156 BladWzgl: 2.70131099816915045875e-18
x: 17102 Czeb: 7.69106901119657084876e+173
Clen1: 7.69106901119657096192e+173 BladClen1: 1.1316189892871551952e+157 BladWzgl: 1.47134161407179825418e-17
Clen2: 7.69106901119657096246e+173 BladClen2: 1.13698211245913223404e+157 BladWzgl: 1.47831479

...

Clen2: 1.78299442489293761992e+200 BladClen2: -1.90877716168525676092e+183 BladWzgl: 1.07054578244117163737e-17
x: 84602 Czeb: 1.86495509381988560974e+200
Clen1: 1.8649550938198856119e+200 BladClen1: 2.15774809581811633843e+182 BladWzgl: 1.15699734699698255043e-18
Clen2: 1.86495509381988561207e+200 BladClen2: 2.32372871857335605677e+182 BladWzgl: 1.24599714291982736203e-18
x: 84702 Czeb: 1.95057976851883703288e+200
Clen1: 1.95057976851883706209e+200 BladClen1: 2.92125896049221904279e+183 BladWzgl: 1.49763624520234944683e-17
Clen2: 1.95057976851883706309e+200 BladClen2: 3.0208473341453628738e+183 BladWzgl: 1.54869202628879317797e-17
x: 84802 Czeb: 2.04002762778954688244e+200
Clen1: 2.04002762778954688792e+200 BladClen1: 5.47736055092291070524e+182 BladWzgl: 2.68494429992492513625e-18
Clen2: 2.04002762778954688759e+200 BladClen2: 5.14539930541243126856e+182 BladWzgl: 2.5222204029597781583e-18
x: 84902 Czeb: 2.13346456561884328715e+200
Clen1: 2.13346456561884332998e+200 BladClen1: 4.28230

Clen1: 9.90293397132444883486e+200 BladClen1: 3.45239695330898614148e+183 BladWzgl: 3.48623646618866829726e-18
Clen2: 9.9029339713244488342e+200 BladClen2: 3.38600470420689025415e+183 BladWzgl: 3.41919345722350159925e-18
x: 88502 Czeb: 1.03376465069338493874e+201
Clen1: 1.03376465069338493887e+201 BladClen1: 1.32784498204191774672e+182 BladWzgl: 1.28447512801998214849e-19
Clen2: 1.03376465069338493927e+201 BladClen2: 5.3113799281676709869e+182 BladWzgl: 5.13790051207992859394e-19
x: 88602 Czeb: 1.07909182337522165822e+201
Clen1: 1.07909182337522162781e+201 BladClen1: -3.04076500887599164e+184 BladWzgl: 2.81789273443383071164e-17
Clen2: 1.07909182337522162834e+201 BladClen2: -2.98765120959431493013e+184 BladWzgl: 2.76867190064459349393e-17
x: 88702 Czeb: 1.12635191996977867184e+201
Clen1: 1.12635191996977865246e+201 BladClen1: -1.93865367378119991022e+184 BladWzgl: 1.72117935736569458356e-17
Clen2: 1.12635191996977865266e+201 BladClen2: -1.91873599905057114402e+184 BladWzgl: 1.703496007

Clen2: 4.90159500456492866491e+201 BladClen2: 7.75461469512479964087e+184 BladWzgl: 1.58205944960830326307e-17
x: 92302 Czeb: 5.10771522689394506741e+201
Clen1: 5.10771522689394503714e+201 BladClen1: -3.02748655905557246253e+184 BladWzgl: 5.92728142539109141622e-18
Clen2: 5.10771522689394503714e+201 BladClen2: -3.02748655905557246253e+184 BladWzgl: 5.92728142539109141622e-18
x: 92402 Czeb: 5.3222657544143529328e+201
Clen1: 5.3222657544143530061e+201 BladClen1: 7.32970430087138596192e+184 BladWzgl: 1.37717743515382310854e-17
Clen2: 5.32226575441435300875e+201 BladClen2: 7.59527329727976951126e+184 BladWzgl: 1.42707516831157032257e-17
x: 92502 Czeb: 5.5455816981260047166e+201
Clen1: 5.5455816981260047506e+201 BladClen1: 3.39928315402730943161e+184 BladWzgl: 6.12971431865482209688e-18
Clen2: 5.54558169812600475113e+201 BladClen2: 3.45239695330898614148e+184 BladWzgl: 6.22549110488380369212e-18
x: 92602 Czeb: 5.77801110568541996939e+201
Clen1: 5.77801110568541993646e+201 BladClen1: -3.2930

Clen2: 2.36611924730848893071e+202 BladClen2: -5.05643369161562277952e+185 BladWzgl: 2.13701557830080785482e-17
x: 96202 Czeb: 2.4615024782811011471e+202
Clen1: 2.46150247828110109207e+202 BladClen1: -5.50258960558170714242e+185 BladWzgl: 2.2354597056608434805e-17
Clen2: 2.46150247828110109165e+202 BladClen2: -5.54508064500704851032e+185 BladWzgl: 2.25272194277019362316e-17
x: 96302 Czeb: 2.56062566676234481024e+202
Clen1: 2.56062566676234484381e+202 BladClen1: 3.35679211460196806372e+185 BladWzgl: 1.31092652790842955977e-17
Clen2: 2.56062566676234484338e+202 BladClen2: 3.31430107517662669582e+185 BladWzgl: 1.29433252122604437546e-17
x: 96402 Czeb: 2.66363134189592142399e+202
Clen1: 2.66363134189592145565e+202 BladClen1: 3.16558243718793190819e+185 BladWzgl: 1.18844615896985630681e-17
Clen2: 2.66363134189592145501e+202 BladClen2: 3.10184587804991985635e+185 BladWzgl: 1.16451771281610081071e-17
x: 96502 Czeb: 2.77066730813937229544e+202
Clen1: 2.7706673081393722487e+202 BladClen1: -4.67

Sredni błąd względny dla Clen2 wynosił: 1.03573948612679605078e-17

In [194]:
start = 0.95
iter = -0.001
finish = -0.95

-0.95

In [195]:
w2 = [0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
blad(2,w2)

Wyniki dla 2. wielomianu Czebyszwa:
x: 0.95 Czeb: 23.7309923939139012627
Clen1: 3.79999999999999982236 BladClen1: -19.9309923939139014403 BladWzgl: 0.839871846194912793557
Clen2: 3.79999999999999982236 BladClen2: -19.9309923939139014403 BladWzgl: 0.839871846194912793557
x: 0.949 Czeb: 23.4664305848195905001
Clen1: 3.79599999999999981881 BladClen1: -19.6704305848195906813 BladWzgl: 0.838237008978449911175
Clen2: 3.79599999999999981881 BladClen2: -19.6704305848195906813 BladWzgl: 0.838237008978449911175
x: 0.948 Czeb: 23.2092514180146456734
Clen1: 3.79199999999999981526 BladClen1: -19.4172514180146458581 BladWzgl: 0.836616876102401530759
Clen2: 3.79199999999999981526 BladClen2: -19.4172514180146458581 BladWzgl: 0.836616876102401530759
x: 0.947 Czeb: 22.9591080163332966549
Clen1: 3.78799999999999981171 BladClen1: -19.1711080163332968432 BladWzgl: 0.835011011869224809468
Clen2: 3.78799999999999981171 BladClen2: -19.1711080163332968432 BladWzgl: 0.835011011869224809468
x: 0.946 Czeb: 22.715

Clen2: 3.62800000000000011369 BladClen2: -12.8006225078481988885 BladWzgl: 0.779165904002794501972
x: 0.906 Czeb: 16.3187057058730523289
Clen1: 3.62400000000000011013 BladClen1: -12.6947057058730522188 BladWzgl: 0.777923564201802255572
Clen2: 3.62400000000000011013 BladClen2: -12.6947057058730522188 BladWzgl: 0.777923564201802255572
x: 0.905 Czeb: 16.2104196510503079445
Clen1: 3.62000000000000010658 BladClen1: -12.5904196510503078379 BladWzgl: 0.776686842294952399751
Clen2: 3.62000000000000010658 BladClen2: -12.5904196510503078379 BladWzgl: 0.776686842294952399751
x: 0.904 Czeb: 16.1037224682162670823
Clen1: 3.61600000000000010303 BladClen1: -12.4877224682162669793 BladWzgl: 0.775455643430464107901
Clen2: 3.61600000000000010303 BladClen2: -12.4877224682162669793 BladWzgl: 0.775455643430464107901
x: 0.903 Czeb: 15.9985737869503520459
Clen1: 3.61200000000000009948 BladClen1: -12.3865737869503519464 BladWzgl: 0.774229875231364639146
Clen2: 3.61200000000000009948 BladClen2: -12.38657378695

Clen1: 3.45199999999999995737 BladClen1: -9.27766371652316693304 BladWzgl: 0.728822372933600220036
Clen2: 3.45199999999999995737 BladClen2: -9.27766371652316693304 BladWzgl: 0.728822372933600220036
x: 0.862 Czeb: 12.6653603964125108525
Clen1: 3.44799999999999995381 BladClen1: -9.21736039641251089869 BladWzgl: 0.72776139864313273061
Clen2: 3.44799999999999995381 BladClen2: -9.21736039641251089869 BladWzgl: 0.72776139864313273061
x: 0.861 Czeb: 12.6016939868467476027
Clen1: 3.44399999999999995026 BladClen1: -9.15769398684674765243 BladWzgl: 0.726703409589636204217
Clen2: 3.44399999999999995026 BladClen2: -9.15769398684674765243 BladWzgl: 0.726703409589636204217
x: 0.86 Czeb: 12.5386533795072487628
Clen1: 3.43999999999999994671 BladClen1: -9.09865337950724881611 BladWzgl: 0.72564836941563280921
Clen2: 3.43999999999999994671 BladClen2: -9.09865337950724881611 BladWzgl: 0.72564836941563280921
x: 0.859 Czeb: 12.476227739582548033
Clen1: 3.43599999999999994316 BladClen1: -9.040227739582548089

x: 0.819 Czeb: 10.3853456423220306742
Clen1: 3.27599999999999980105 BladClen1: -7.10934564232203087316 BladWzgl: 0.684555515740395903392
Clen2: 3.27599999999999980105 BladClen2: -7.10934564232203087316 BladWzgl: 0.684555515740395903392
x: 0.818 Czeb: 10.3412857916303511374
Clen1: 3.2719999999999997975 BladClen1: -7.06928579163035133992 BladWzgl: 0.683598339130307123049
Clen2: 3.2719999999999997975 BladClen2: -7.06928579163035133992 BladWzgl: 0.683598339130307123049
x: 0.817 Czeb: 10.29755135836389166
Clen1: 3.26799999999999979394 BladClen1: -7.02955135836389186609 BladWzgl: 0.682643000625031092106
Clen2: 3.26799999999999979394 BladClen2: -7.02955135836389186609 BladWzgl: 0.682643000625031092106
x: 0.816 Czeb: 10.2541380660814599292
Clen1: 3.26399999999999979039 BladClen1: -6.99013806608146013883 BladWzgl: 0.681689481947134313315
Clen2: 3.26399999999999979039 BladClen2: -6.99013806608146013883 BladWzgl: 0.681689481947134313315
x: 0.815 Czeb: 10.2110417183053819035
Clen1: 3.2599999999999

Clen1: 3.10400000000000009237 BladClen1: -5.63615599730021231504 BladWzgl: 0.644857597397711305781
Clen2: 3.10400000000000009237 BladClen2: -5.63615599730021231504 BladWzgl: 0.644857597397711305781
x: 0.775 Czeb: 8.70702143228223798561
Clen1: 3.10000000000000008882 BladClen1: -5.60702143228223789679 BladWzgl: 0.643965502541844021333
Clen2: 3.10000000000000008882 BladClen2: -5.60702143228223789679 BladWzgl: 0.643965502541844021333
x: 0.774 Czeb: 8.67408233497828362862
Clen1: 3.09600000000000008527 BladClen1: -5.57808233497828354335 BladWzgl: 0.643074635397987468043
Clen2: 3.09600000000000008527 BladClen2: -5.57808233497828354335 BladWzgl: 0.643074635397987468043
x: 0.773 Czeb: 8.64133664403804633864
Clen1: 3.09200000000000008171 BladClen1: -5.54933664403804625693 BladWzgl: 0.642184985104905429185
Clen2: 3.09200000000000008171 BladClen2: -5.54933664403804625693 BladWzgl: 0.642184985104905429185
x: 0.772 Czeb: 8.60878232928342003796
Clen1: 3.08800000000000007816 BladClen1: -5.520782329283

...

Clen1: -2.97599999999999997868 BladClen1: 4.79158804262944920671 BladWzgl: 0.616869485911539438389
Clen2: -2.97599999999999997868 BladClen2: 4.79158804262944920671 BladWzgl: 0.616869485911539438389
x: -0.745 Czeb: -7.79549844964588333103
Clen1: -2.97999999999999998224 BladClen1: 4.81549844964588334879 BladWzgl: 0.617728100486586738534
Clen2: -2.97999999999999998224 BladClen2: 4.81549844964588334879 BladWzgl: 0.617728100486586738534
x: -0.746 Czeb: -7.82355392187616582823
Clen1: -2.98399999999999998579 BladClen1: 4.83955392187616584244 BladWzgl: 0.61858766108121778128
Clen2: -2.98399999999999998579 BladClen2: 4.83955392187616584244 BladWzgl: 0.61858766108121778128
x: -0.747 Czeb: -7.85175581884301701865
Clen1: -2.98799999999999998934 BladClen1: 4.86375581884301702931 BladWzgl: 0.619448175804288833147
Clen2: -2.98799999999999998934 BladClen2: 4.86375581884301702931 BladWzgl: 0.619448175804288833147
x: -0.748 Czeb: -7.88010551859091435941
Clen1: -2.99199999999999999289 BladClen1: 4.888105

Clen2: -3.14800000000000013145 BladClen2: 5.97015978057182202486 BladWzgl: 0.654754898383390542785
x: -0.788 Czeb: -9.15381298838987186601
Clen1: -3.152000000000000135 BladClen1: 6.00181298838987173101 BladWzgl: 0.655662617971570834828
Clen2: -3.152000000000000135 BladClen2: 6.00181298838987173101 BladWzgl: 0.655662617971570834828
x: -0.789 Czeb: -9.18969160377604136602
Clen1: -3.15600000000000013856 BladClen1: 6.03369160377604122746 BladWzgl: 0.656571717955888667763
Clen2: -3.15600000000000013856 BladClen2: 6.03369160377604122746 BladWzgl: 0.656571717955888667763
x: -0.79 Czeb: -9.22579819749773221219
Clen1: -3.16000000000000014211 BladClen1: 6.06579819749773207008 BladWzgl: 0.657482211039791508559
Clen2: -3.16000000000000014211 BladClen2: 6.06579819749773207008 BladWzgl: 0.657482211039791508559
x: -0.791 Czeb: -9.26213538266905148273
Clen1: -3.16400000000000014566 BladClen1: 6.09813538266905133707 BladWzgl: 0.658394110075269010061
Clen2: -3.16400000000000014566 BladClen2: 6.098135382

Clen1: -3.38399999999999989697 BladClen1: 8.33217479351549113794 BladWzgl: 0.711168529008893742351
Clen2: -3.38399999999999989697 BladClen2: 8.33217479351549113794 BladWzgl: 0.711168529008893742351
x: -0.847 Czeb: -11.771481758784048185
Clen1: -3.38799999999999990052 BladClen1: 8.38348175878404828446 BladWzgl: 0.712185766462932688594
Clen2: -3.38799999999999990052 BladClen2: 8.38348175878404828446 BladWzgl: 0.712185766462932688594
x: -0.848 Czeb: -11.8272842102265240364
Clen1: -3.39199999999999990408 BladClen1: 8.43528421022652413232 BladWzgl: 0.7132055051939067204
Clen2: -3.39199999999999990408 BladClen2: 8.43528421022652413232 BladWzgl: 0.7132055051939067204
x: -0.849 Czeb: -11.8835901057434858092
Clen1: -3.39599999999999990763 BladClen1: 8.48759010574348590154 BladWzgl: 0.714227773780360264877
Clen2: -3.39599999999999990763 BladClen2: 8.48759010574348590154 BladWzgl: 0.714227773780360264877
x: -0.85 Czeb: -11.9404075865664360935
Clen1: -3.39999999999999991118 BladClen1: 8.5404075865

Clen2: -3.55600000000000004974 BladClen2: 11.1135314270186666523 BladWzgl: 0.757592802626914123645
x: -0.89 Czeb: -14.7565406145577000382
Clen1: -3.56000000000000005329 BladClen1: 11.1965406145576999849 BladWzgl: 0.758751045181418053045
Clen2: -3.56000000000000005329 BladClen2: 11.1965406145576999849 BladWzgl: 0.758751045181418053045
x: -0.891 Czeb: -14.8446584888766027911
Clen1: -3.56400000000000005684 BladClen1: 11.2806584888766027342 BladWzgl: 0.759913641484539641863
Clen2: -3.56400000000000005684 BladClen2: 11.2806584888766027342 BladWzgl: 0.759913641484539641863
x: -0.892 Czeb: -14.9339101475901594096
Clen1: -3.5680000000000000604 BladClen1: 11.3659101475901593492 BladWzgl: 0.761080657059145518502
Clen2: -3.5680000000000000604 BladClen2: 11.3659101475901593492 BladWzgl: 0.761080657059145518502
x: -0.893 Czeb: -15.0243215008448121025
Clen1: -3.57200000000000006395 BladClen1: 11.4523215008448120385 BladWzgl: 0.762252158954456092367
Clen2: -3.57200000000000006395 BladClen2: 11.452321

x: -0.933 Czeb: -20.0456508075569306681
Clen1: -3.73200000000000020606 BladClen1: 16.313650807556930462 BladWzgl: 0.813824952064260828276
Clen2: -3.73200000000000020606 BladClen2: 16.313650807556930462 BladWzgl: 0.813824952064260828276
x: -0.934 Czeb: -20.2238173658803898486
Clen1: -3.73600000000000020961 BladClen1: 16.487817365880389639 BladWzgl: 0.815267319101535832494
Clen2: -3.73600000000000020961 BladClen2: 16.487817365880389639 BladWzgl: 0.815267319101535832494
x: -0.935 Czeb: -20.4058837668867629981
Clen1: -3.74000000000000021316 BladClen1: 16.6658837668867627849 BladWzgl: 0.816719528410280866794
Clen2: -3.74000000000000021316 BladClen2: 16.6658837668867627849 BladWzgl: 0.816719528410280866794
x: -0.936 Czeb: -20.5920000000000101952
Clen1: -3.74400000000000021672 BladClen1: 16.8480000000000099784 BladWzgl: 0.818181818181818261339
Clen2: -3.74400000000000021672 BladClen2: 16.8480000000000099784 BladWzgl: 0.818181818181818261339
x: -0.937 Czeb: -20.7823243150641929593
Clen1: -3.74

In [196]:
w20 = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
blad(20,w20)

Wyniki dla 20. wielomianu Czebyszwa:
x: 0.95 Czeb: 27.1883326457487375163
Clen1: 4.35361751160232742647 BladClen1: -22.8347151341464100899 BladWzgl: 0.839871846194912793232
Clen2: 4.35361751160232748892 BladClen2: -22.8347151341464100274 BladWzgl: 0.839871846194912790955
x: 0.949 Czeb: 51.5233913246345497303
Clen1: 8.33457788824667040496 BladClen1: -43.188813436387879327 BladWzgl: 0.838237008978449911229
Clen2: 8.33457788824667042404 BladClen2: -43.1888134363878793062 BladWzgl: 0.838237008978449910849
x: 0.948 Czeb: 74.4886908940873242735
Clen1: 12.1701950133185841625 BladClen1: -62.3184958807687401118 BladWzgl: 0.836616876102401531247
Clen2: 12.1701950133185842207 BladClen2: -62.3184958807687400528 BladWzgl: 0.836616876102401530433
x: 0.947 Czeb: 96.0815272771674746127
Clen1: 15.8523939635193371342 BladClen1: -80.2291333136481374794 BladWzgl: 0.835011011869224809955
Clen2: 15.8523939635193371611 BladClen2: -80.2291333136481374516 BladWzgl: 0.83501101186922480963
x: 0.946 Czeb: 116.304

Clen1: 31.7039677303419845447 BladClen1: -111.860673350911954689 BladWzgl: 0.779165904002794501972
Clen2: 31.7039677303419845412 BladClen2: -111.860673350911954696 BladWzgl: 0.779165904002794502026
x: 0.906 Czeb: 134.376730010493780312
Clen1: 29.8419052549471741087 BladClen1: -104.534824755546606204 BladWzgl: 0.777923564201802255626
Clen2: 29.8419052549471740948 BladClen2: -104.534824755546606218 BladWzgl: 0.777923564201802255735
x: 0.905 Czeb: 125.124401720261405516
Clen1: 27.9419252541064644796 BladClen1: -97.1824764661549410361 BladWzgl: 0.776686842294952399859
Clen2: 27.9419252541064644865 BladClen2: -97.1824764661549410291 BladWzgl: 0.776686842294952399805
x: 0.904 Czeb: 115.830543586215834455
Clen1: 26.0090948806664169768 BladClen1: -89.821448705549417478 BladWzgl: 0.775455643430464108064
Clen2: 26.0090948806664169941 BladClen2: -89.8214487055494174572 BladWzgl: 0.775455643430464107901
x: 0.903 Czeb: 106.517090163280364862
Clen1: 24.0483767361557902661 BladClen1: -82.468713427124

Clen2: -35.8904663532900313552 BladClen2: 96.9812672379484715726 BladWzgl: 0.72988636948395598311
x: 0.863 Czeb: -134.278309444230160866
Clen1: -36.413273321574074072 BladClen1: 97.8650361226560867936 BladWzgl: 0.728822372933600219982
Clen2: -36.4132733215740740755 BladClen2: 97.8650361226560867867 BladWzgl: 0.728822372933600219928
x: 0.862 Czeb: -135.448001086544461136
Clen1: -36.8741743723843023103 BladClen1: 98.5738267141601588253 BladWzgl: 0.727761398643132730664
Clen2: -36.8741743723843023103 BladClen2: 98.5738267141601588253 BladWzgl: 0.727761398643132730664
x: 0.861 Czeb: -136.384784032498528036
Clen1: -37.2734964599356745386 BladClen1: 99.1112875725628535012 BladWzgl: 0.72670340958963620438
Clen2: -37.2734964599356745421 BladClen2: 99.1112875725628534943 BladWzgl: 0.726703409589636204326
x: 0.86 Czeb: -137.092866828139069213
Clen1: -37.6116515557854569698 BladClen1: 99.4812152723536122431 BladWzgl: 0.72564836941563280921
Clen2: -37.6116515557854569629 BladClen2: 99.481215272353

Clen1: -12.9176598764510685777 BladClen1: 28.1578806126071024517 BladWzgl: 0.685514548983424464078
Clen2: -12.9176598764510685707 BladClen2: 28.1578806126071024586 BladWzgl: 0.685514548983424464241
x: 0.819 Czeb: -37.241371144224401521
Clen1: -11.7475851137103684471 BladClen1: 25.4937860305140330738 BladWzgl: 0.684555515740395902958
Clen2: -11.7475851137103684436 BladClen2: 25.4937860305140330773 BladWzgl: 0.684555515740395903012
x: 0.818 Czeb: -33.4133081562484233057
Clen1: -10.5720261957878566283 BladClen1: 22.8412819604605666773 BladWzgl: 0.683598339130307122344
Clen2: -10.5720261957878566214 BladClen2: 22.8412819604605666843 BladWzgl: 0.683598339130307122561
x: 0.817 Czeb: -29.5958567810023585043
Clen1: -9.39245230195023479529 BladClen1: 20.203404479052123709 BladWzgl: 0.682643000625031092323
Clen2: -9.39245230195023480396 BladClen2: 20.2034044790521237003 BladWzgl: 0.682643000625031092052
x: 0.816 Czeb: -25.7934050082154223936
Clen1: -8.21031211051243144626 BladClen1: 17.583092897

Clen2: 27.5880628287274690617 BladClen2: -50.2895245487855238539 BladWzgl: 0.645750930945076113293
x: 0.776 Czeb: 78.8962061184323730223
Clen1: 28.019388197105462383 BladClen1: -50.8768179213269106376 BladWzgl: 0.644857597397711305889
Clen2: 28.019388197105462383 BladClen2: -50.8768179213269106376 BladWzgl: 0.644857597397711305889
x: 0.775 Czeb: 79.8242287452770457878
Clen1: 28.420179166309601778 BladClen1: -51.4040495789674440098 BladWzgl: 0.643965502541844021171
Clen2: 28.4201791663096017728 BladClen2: -51.4040495789674440133 BladWzgl: 0.643965502541844021225
x: 0.774 Czeb: 80.6620597462237204078
Clen1: 28.7903350844702198511 BladClen1: -51.8717246617535005584 BladWzgl: 0.643074635397987468097
Clen2: 28.7903350844702198511 BladClen2: -51.8717246617535005584 BladWzgl: 0.643074635397987468097
x: 0.773 Czeb: 81.4101846852709618921
Clen1: 29.1297864457726291415 BladClen1: -52.2803982394983327506 BladWzgl: 0.642184985104905429239
Clen2: 29.1297864457726291415 BladClen2: -52.28039823949833

...

Clen1: -28.019388197105462383 BladClen1: 50.876817921326910589 BladWzgl: 0.644857597397711305672
Clen2: -28.019388197105462383 BladClen2: 50.876817921326910589 BladWzgl: 0.644857597397711305672
x: -0.777 Czeb: -77.8775873775129927543
Clen1: -27.5880628287274690547 BladClen1: 50.2895245487855237013 BladWzgl: 0.645750930945076112696
Clen2: -27.5880628287274690617 BladClen2: 50.2895245487855236943 BladWzgl: 0.645750930945076112588
x: -0.778 Czeb: -76.7680513703674449674
Clen1: -27.1263353114292392367 BladClen1: 49.6417160589382057308 BladWzgl: 0.646645514283562556604
Clen2: -27.1263353114292392401 BladClen2: 49.6417160589382057273 BladWzgl: 0.64664551428356255655
x: -0.779 Czeb: -75.5673625215158353413
Clen1: -26.6343699258806797369 BladClen1: 48.9329925956351556027 BladWzgl: 0.647541358634857242135
Clen2: -26.6343699258806797386 BladClen2: 48.9329925956351556027 BladWzgl: 0.647541358634857242135
x: -0.78 Czeb: -74.2753730505085481978
Clen1: -26.11236339397991006 BladClen1: 48.16300965652

Clen1: 11.7475851137103684471 BladClen1: -25.4937860305140329975 BladWzgl: 0.684555515740395902308
Clen2: 11.7475851137103684436 BladClen2: -25.493786030514033001 BladWzgl: 0.684555515740395902362
x: -0.82 Czeb: 41.0755404890581708663
Clen1: 12.9176598764510685777 BladClen1: -28.1578806126071022886 BladWzgl: 0.685514548983424462831
Clen2: 12.9176598764510685707 BladClen2: -28.1578806126071022956 BladWzgl: 0.685514548983424462994
x: -0.821 Czeb: 44.9111956713393329146
Clen1: 14.0807620695559421991 BladClen1: -30.8304336017833907155 BladWzgl: 0.686475457643142537606
Clen2: 14.0807620695559422112 BladClen2: -30.8304336017833907034 BladWzgl: 0.686475457643142537335
x: -0.822 Czeb: 48.7436031156947708505
Clen1: 15.2353853664720236064 BladClen1: -33.5082177492227472441 BladWzgl: 0.687438260763976253284
Clen2: 15.2353853664720236168 BladClen2: -33.5082177492227472337 BladWzgl: 0.687438260763976253067
x: -0.823 Czeb: 52.5679186089489461596
Clen1: 16.3800069093591858568 BladClen1: -36.187911699

Clen2: 36.8741743723843023103 BladClen2: -98.5738267141601588253 BladWzgl: 0.727761398643132730664
x: -0.863 Czeb: 134.278309444230160949
Clen1: 36.413273321574074072 BladClen1: -97.8650361226560868769 BladWzgl: 0.728822372933600220145
Clen2: 36.4132733215740740755 BladClen2: -97.8650361226560868699 BladWzgl: 0.728822372933600220091
x: -0.864 Czeb: 132.871733591238502928
Clen1: 35.8904663532900313552 BladClen1: -96.9812672379484715726 BladWzgl: 0.72988636948395598311
Clen2: 35.8904663532900313552 BladClen2: -96.9812672379484715726 BladWzgl: 0.72988636948395598311
x: -0.865 Czeb: 131.224546441229506857
Clen1: 35.3055146447400473204 BladClen1: -95.9190317964894595404 BladWzgl: 0.730953425999822013867
Clen2: 35.305514644740047317 BladClen2: -95.9190317964894595404 BladWzgl: 0.730953425999822013867
x: -0.866 Czeb: 129.333285068437368381
Clen1: 34.6582706047130168145 BladClen1: -94.6750144637243515669 BladWzgl: 0.732023580887368507659
Clen2: 34.6582706047130168145 BladClen2: -94.67501446372

x: -0.906 Czeb: -134.376730010493780049
Clen1: -29.8419052549471741087 BladClen1: 104.53482475554660594 BladWzgl: 0.777923564201802255193
Clen2: -29.8419052549471740948 BladClen2: 104.534824755546605954 BladWzgl: 0.777923564201802255301
x: -0.907 Czeb: -143.564641081253939511
Clen1: -31.7039677303419845447 BladClen1: 111.860673350911954967 BladWzgl: 0.779165904002794502405
Clen2: -31.7039677303419845412 BladClen2: 111.860673350911954974 BladWzgl: 0.77916590400279450246
x: -0.908 Czeb: -152.664290750983485112
Clen1: -33.5229471900229960279 BladClen1: 119.141343560960489084 BladWzgl: 0.780413959118288201079
Clen2: -33.5229471900229959863 BladClen2: 119.141343560960489126 BladWzgl: 0.78041395911828820135
x: -0.909 Czeb: -161.650875949569932999
Clen1: -35.2935865873759682908 BladClen1: 126.357289362193964705 BladWzgl: 0.78166782963560015431
Clen2: -35.2935865873759682838 BladClen2: 126.357289362193964719 BladWzgl: 0.781667829635600154364
x: -0.91 Czeb: -170.498634701675023245
Clen1: -37.01

Clen1: -8.33457788824667040496 BladClen1: 43.1888134363878792715 BladWzgl: 0.838237008978449911066
Clen2: -8.33457788824667042404 BladClen2: 43.1888134363878792507 BladWzgl: 0.838237008978449910633
x: -0.95 Czeb: -27.1883326457487378095
Clen1: -4.35361751160232742647 BladClen1: 22.834715134146410383 BladWzgl: 0.839871846194912794966
Clen2: -4.35361751160232748892 BladClen2: 22.8347151341464103206 BladWzgl: 0.83987184619491279269
Sredni błąd względny dla Clen1 wynosił: 0.405506777514457257642
Sredni błąd względny dla Clen2 wynosił: 0.405506777514457257588

In [197]:
w39 = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1]
blad(39,w39)

Wyniki dla 39. wielomianu Czebyszwa:
x: 0.95 Czeb: -140.804649269779382989
Clen1: -22.5467885347425931047 BladClen1: 118.257860735036789884 BladWzgl: 0.839871846194912793178
Clen2: -22.5467885347425928688 BladClen2: 118.25786073503679012 BladWzgl: 0.839871846194912794858
x: 0.949 Czeb: -43.7297971318315985209
Clen1: -7.07386278081068164275 BladClen1: 36.6559343510209168782 BladWzgl: 0.838237008978449912421
Clen2: -7.0738627808106817052 BladClen2: 36.6559343510209168157 BladWzgl: 0.838237008978449911012
x: 0.948 Czeb: 49.3892653271610955687
Clen1: 8.06937245615892548636 BladClen1: -41.3198928710021700823 BladWzgl: 0.836616876102401530488
Clen2: 8.06937245615892551065 BladClen2: -41.319892871002170058 BladWzgl: 0.83661687610240153
x: 0.947 Czeb: 137.431804902467872356
Clen1: 22.6747344278442833077 BladClen1: -114.757070474623589049 BladWzgl: 0.835011011869224810389
Clen2: 22.6747344278442833077 BladClen2: -114.757070474623589049 BladWzgl: 0.835011011869224810389
x: 0.946 Czeb: 219.442761

Clen1: -87.7364843499779352431 BladClen1: 309.559431182414216105 BladWzgl: 0.779165904002794501972
Clen2: -87.736484349977935257 BladClen2: 309.559431182414216077 BladWzgl: 0.779165904002794501917
x: 0.906 Czeb: -403.642281396465752608
Clen1: -89.6394391899802944895 BladClen1: 314.002842206485458132 BladWzgl: 0.777923564201802255626
Clen2: -89.6394391899802945103 BladClen2: 314.002842206485458104 BladWzgl: 0.777923564201802255572
x: 0.905 Czeb: -406.422644554766561958
Clen1: -90.7595241183610905583 BladClen1: 315.663120436405471414 BladWzgl: 0.776686842294952399859
Clen2: -90.7595241183610905653 BladClen2: 315.663120436405471386 BladWzgl: 0.776686842294952399751
x: 0.904 Czeb: -405.740991920808222682
Clen1: -91.1068499647431431568 BladClen1: 314.634141956065079532 BladWzgl: 0.775455643430464107901
Clen2: -91.1068499647431430943 BladClen2: 314.634141956065079587 BladWzgl: 0.775455643430464108064
x: 0.903 Czeb: -401.725078114393919726
Clen1: -90.6975210085765018164 BladClen1: 311.0275571

Clen2: 76.5011371623244597756 BladClen2: -206.717214374291163817 BladWzgl: 0.729886369483955983165
x: 0.863 Czeb: 276.863106985029951035
Clen1: 75.0790803744311959975 BladClen1: -201.78402661059875503 BladWzgl: 0.728822372933600220145
Clen2: 75.0790803744311959905 BladClen2: -201.784026610598755044 BladWzgl: 0.728822372933600220199
x: 0.862 Czeb: 268.979906672952972457
Clen1: 73.2267135857454065928 BladClen1: -195.753193087207565865 BladWzgl: 0.727761398643132730556
Clen2: 73.2267135857454066067 BladClen2: -195.753193087207565851 BladWzgl: 0.727761398643132730501
x: 0.861 Czeb: 259.652321975745295934
Clen1: 70.9620942881051645287 BladClen1: -188.690227687640131399 BladWzgl: 0.726703409589636204163
Clen2: 70.9620942881051645496 BladClen2: -188.690227687640131385 BladWzgl: 0.726703409589636204109
x: 0.86 Czeb: 248.969752709377915703
Clen1: 68.3052576220045024255 BladClen1: -180.664495087373413285 BladWzgl: 0.725648369415632809318
Clen2: 68.3052576220045024186 BladClen2: -180.664495087373

Clen1: 47.8135688050059153922 BladClen1: -90.3154736706495913715 BladWzgl: 0.653848546633972380537
Clen2: 47.8135688050059154269 BladClen2: -90.3154736706495913368 BladWzgl: 0.653848546633972380266
x: 0.785 Czeb: 144.665692118119008358
Clen1: 50.2071614985195985859 BladClen1: -94.4585306195994097722 BladWzgl: 0.652943550309594932153
Clen2: 50.2071614985195986067 BladClen2: -94.4585306195994097514 BladWzgl: 0.65294355030959493199
x: 0.784 Czeb: 150.557309667177451687
Clen1: 52.387936958443633538 BladClen1: -98.1693727087338181489 BladWzgl: 0.652039897137823452867
Clen2: 52.3879369584436335623 BladClen2: -98.1693727087338181281 BladWzgl: 0.652039897137823452704
x: 0.783 Czeb: 155.790632364241008037
Clen1: 54.3494978011795513186 BladClen1: -101.441134563061456722 BladWzgl: 0.651137574985191985345
Clen2: 54.3494978011795512908 BladClen2: -101.44113456306145675 BladWzgl: 0.651137574985191985508
x: 0.782 Czeb: 160.355218299863633721
Clen1: 56.0863908735107806851 BladClen1: -104.2688274263528

Clen2: -18.4736905275962750884 BladClen2: 29.6363581044247398726 BladWzgl: 0.616011809322915888931
x: 0.742 Czeb: -56.1847044126778088213
Clen1: -21.6223990434213214594 BladClen1: 34.5623053692564873619 BladWzgl: 0.615155062762200259649
Clen2: -21.6223990434213214733 BladClen2: 34.5623053692564873481 BladWzgl: 0.615155062762200259378
x: 0.741 Czeb: -63.9942484023408085722
Clen1: -24.6826303503549368823 BladClen1: 39.3116180519858716899 BladWzgl: 0.614299238344487139388
Clen2: -24.6826303503549368719 BladClen2: 39.3116180519858717003 BladWzgl: 0.61429923834448713955
x: 0.74 Czeb: -71.5158118482778346336
Clen1: -27.6448426892237239388 BladClen1: 43.8709691590541106948 BladWzgl: 0.613444328257465810647
Clen2: -27.6448426892237239527 BladClen2: 43.8709691590541106809 BladWzgl: 0.61344432825746581043
x: 0.739 Czeb: -78.7278482032108008412
Clen1: -30.4999301047166809092 BladClen1: 48.227918098494119932 BladWzgl: 0.612590324760422124718
Clen2: -30.4999301047166809057 BladClen2: 48.22791809849

...

Clen1: 61.1749234305195688857 BladClen1: -109.793093237129333641 BladWzgl: 0.642184985104905429294
Clen2: 61.1749234305195688961 BladClen2: -109.793093237129333634 BladWzgl: 0.642184985104905429294
x: -0.774 Czeb: 172.446447501091106619
Clen1: 61.550511148648756124 BladClen1: -110.895936352442350495 BladWzgl: 0.643074635397987467988
Clen2: 61.550511148648756124 BladClen2: -110.895936352442350495 BladWzgl: 0.643074635397987467988
x: -0.775 Czeb: 173.281866862380837344
Clen1: 61.694322386958852969 BladClen1: -111.587544475421984375 BladWzgl: 0.643965502541844021171
Clen2: 61.6943223869588529447 BladClen2: -111.587544475421984402 BladWzgl: 0.643965502541844021333
x: -0.776 Czeb: 173.461563322282437433
Clen1: 61.6035563574244234321 BladClen1: -111.858006964858014004 BladWzgl: 0.644857597397711305727
Clen2: 61.6035563574244234286 BladClen2: -111.858006964858014004 BladWzgl: 0.644857597397711305727
x: -0.777 Czeb: 172.975099216939928348
Clen1: 61.2762678672840634397 BladClen1: -111.698831349

Clen2: -59.989922358973398777 BladClen2: 128.47360289912110505 BladWzgl: 0.681689481947134313857
x: -0.817 Czeb: -195.643736504242088919
Clen1: -62.0889091634933384389 BladClen1: 133.55482734074875048 BladWzgl: 0.68264300062503109151
Clen2: -62.0889091634933384424 BladClen2: 133.55482734074875048 BladWzgl: 0.68264300062503109151
x: -0.818 Czeb: -202.017427432308204233
Clen1: -63.9186495642049711322 BladClen1: 138.098777868103233107 BladWzgl: 0.683598339130307122941
Clen2: -63.9186495642049711217 BladClen2: 138.098777868103233107 BladWzgl: 0.683598339130307122941
x: -0.819 Czeb: -207.540130781704203991
Clen1: -65.4673895176054674513 BladClen1: 142.072741264098736547 BladWzgl: 0.684555515740395903338
Clen2: -65.4673895176054674444 BladClen2: 142.072741264098736547 BladWzgl: 0.684555515740395903338
x: -0.82 Czeb: -212.170275211818087885
Clen1: -66.7244646922995679195 BladClen1: 145.445810519518519965 BladWzgl: 0.685514548983424464078
Clen2: -66.7244646922995679195 BladClen2: 145.445810519

x: -0.86 Czeb: 248.969752709377915231
Clen1: 68.3052576220045024255 BladClen1: -180.664495087373412813 BladWzgl: 0.725648369415632808776
Clen2: 68.3052576220045024186 BladClen2: -180.664495087373412813 BladWzgl: 0.725648369415632808776
x: -0.861 Czeb: 259.652321975745295712
Clen1: 70.9620942881051645287 BladClen1: -188.690227687640131177 BladWzgl: 0.726703409589636203892
Clen2: 70.9620942881051645496 BladClen2: -188.690227687640131163 BladWzgl: 0.726703409589636203838
x: -0.862 Czeb: 268.979906672952972291
Clen1: 73.2267135857454065928 BladClen1: -195.753193087207565698 BladWzgl: 0.727761398643132730393
Clen2: 73.2267135857454066067 BladClen2: -195.753193087207565684 BladWzgl: 0.727761398643132730339
x: -0.863 Czeb: 276.863106985029950896
Clen1: 75.0790803744311959975 BladClen1: -201.784026610598754892 BladWzgl: 0.728822372933600219982
Clen2: 75.0790803744311959905 BladClen2: -201.784026610598754906 BladWzgl: 0.728822372933600220036
x: -0.864 Czeb: 283.218351536615623731
Clen1: 76.5011

Clen1: -90.6975210085765018164 BladClen1: 311.02755710581741791 BladWzgl: 0.774229875231364639146
Clen2: -90.6975210085765018372 BladClen2: 311.027557105817417882 BladWzgl: 0.774229875231364639092
x: -0.904 Czeb: -405.740991920808222709
Clen1: -91.1068499647431431568 BladClen1: 314.634141956065079559 BladWzgl: 0.775455643430464107956
Clen2: -91.1068499647431430943 BladClen2: 314.634141956065079615 BladWzgl: 0.775455643430464108064
x: -0.905 Czeb: -406.422644554766562291
Clen1: -90.7595241183610905583 BladClen1: 315.663120436405471747 BladWzgl: 0.776686842294952400022
Clen2: -90.7595241183610905653 BladClen2: 315.663120436405471719 BladWzgl: 0.776686842294952399968
x: -0.906 Czeb: -403.642281396465752497
Clen1: -89.6394391899802944895 BladClen1: 314.002842206485458021 BladWzgl: 0.777923564201802255572
Clen2: -89.6394391899802945103 BladClen2: 314.002842206485457993 BladWzgl: 0.777923564201802255518
x: -0.907 Czeb: -397.295915532392151376
Clen1: -87.7364843499779352431 BladClen1: 309.559

Clen2: 36.5549944180410088246 BladClen2: -182.887767143435249095 BladWzgl: 0.833419001119340943163
x: -0.947 Czeb: 137.431804902467872662
Clen1: 22.6747344278442833077 BladClen1: -114.757070474623589354 BladWzgl: 0.835011011869224810769
Clen2: 22.6747344278442833077 BladClen2: -114.757070474623589354 BladWzgl: 0.835011011869224810769
x: -0.948 Czeb: 49.3892653271610991353
Clen1: 8.06937245615892548636 BladClen1: -41.3198928710021736489 BladWzgl: 0.836616876102401542305
Clen2: 8.06937245615892551065 BladClen2: -41.3198928710021736246 BladWzgl: 0.836616876102401541763
x: -0.949 Czeb: -43.7297971318315955441
Clen1: -7.07386278081068164275 BladClen1: 36.6559343510209139014 BladWzgl: 0.838237008978449901417
Clen2: -7.0738627808106817052 BladClen2: 36.6559343510209138389 BladWzgl: 0.838237008978449900007
x: -0.95 Czeb: -140.804649269779378007
Clen1: -22.5467885347425931047 BladClen1: 118.257860735036784902 BladWzgl: 0.839871846194912787485
Clen2: -22.5467885347425928688 BladClen2: 118.257860

In [198]:
start = -2
iter = -100
finish = -100000

-100000

In [199]:
w2 = [0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
blad(2,w2)

Wyniki dla 2. wielomianu Czebyszwa:
x: -2 Czeb: -7.99999999999999999957
Clen1: -8.0 BladClen1: -4.33680868994201773603e-19 BladWzgl: 5.42101086242752217063e-20
Clen2: -8.0 BladClen2: -4.33680868994201773603e-19 BladWzgl: 5.42101086242752217063e-20
x: -102 Czeb: -408.0
Clen1: -408.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -408.0 BladClen2: 0.0 BladWzgl: 0.0
x: -202 Czeb: -808.000000000000000333
Clen1: -808.0 BladClen1: 3.33066907387546962127e-16 BladWzgl: 4.12211519043993764842e-19
Clen2: -808.0 BladClen2: 3.33066907387546962127e-16 BladWzgl: 4.12211519043993764842e-19
x: -302 Czeb: -1208.00000000000000033
Clen1: -1208.0 BladClen1: 3.33066907387546962127e-16 BladWzgl: 2.75717638565850134137e-19
Clen2: -1208.0 BladClen2: 3.33066907387546962127e-16 BladWzgl: 2.75717638565850134137e-19
x: -402 Czeb: -1608.0
Clen1: -1608.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -1608.0 BladClen2: 0.0 BladWzgl: 0.0
x: -502 Czeb: -2007.99999999999999989
Clen1: -2008.0 BladClen1: -1.11022302462515654042e-16 BladWzgl:

Clen2: -18808.0 BladClen2: 1.06581410364015027881e-14 BladWzgl: 5.6668125459386977788e-19
x: -4802 Czeb: -19207.9999999999999964
Clen1: -19208.0 BladClen1: -3.55271367880050092936e-15 BladWzgl: 1.8496010406083407591e-19
Clen2: -19208.0 BladClen2: -3.55271367880050092936e-15 BladWzgl: 1.8496010406083407591e-19
x: -4902 Czeb: -19607.9999999999999964
Clen1: -19608.0 BladClen1: -3.55271367880050092936e-15 BladWzgl: 1.81186948123240561504e-19
Clen2: -19608.0 BladClen2: -3.55271367880050092936e-15 BladWzgl: 1.81186948123240561504e-19
x: -5002 Czeb: -20008.0000000000000053
Clen1: -20008.0 BladClen1: 5.32907051820075139403e-15 BladWzgl: 2.66346987115191493038e-19
Clen2: -20008.0 BladClen2: 5.32907051820075139403e-15 BladWzgl: 2.66346987115191493038e-19
x: -5102 Czeb: -20408.0000000000000124
Clen1: -20408.0 BladClen1: 1.24344978758017532527e-14 BladWzgl: 6.09295270276448120606e-19
Clen2: -20408.0 BladClen2: 1.24344978758017532527e-14 BladWzgl: 6.09295270276448120606e-19
x: -5202 Czeb: -20808.00

x: -9502 Czeb: -38007.9999999999999716
Clen1: -38008.0 BladClen1: -2.84217094304040074348e-14 BladWzgl: 7.47782294001368329187e-19
Clen2: -38008.0 BladClen2: -2.84217094304040074348e-14 BladWzgl: 7.47782294001368329187e-19
x: -9602 Czeb: -38408.0000000000000284
Clen1: -38408.0 BladClen1: 2.84217094304040074348e-14 BladWzgl: 7.39994517558946245942e-19
Clen2: -38408.0 BladClen2: 2.84217094304040074348e-14 BladWzgl: 7.39994517558946245942e-19
x: -9702 Czeb: -38808.0
Clen1: -38808.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -38808.0 BladClen2: 0.0 BladWzgl: 0.0
x: -9802 Czeb: -39208.0
Clen1: -39208.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -39208.0 BladClen2: 0.0 BladWzgl: 0.0
x: -9902 Czeb: -39608.0000000000000213
Clen1: -39608.0 BladClen1: 2.13162820728030055761e-14 BladWzgl: 5.38181227853034880932e-19
Clen2: -39608.0 BladClen2: 2.13162820728030055761e-14 BladWzgl: 5.38181227853034880932e-19
x: -10002 Czeb: -40008.000000000000032
Clen1: -40008.0 BladClen1: 3.19744231092045083642e-14 BladWzgl: 7.99

x: -14302 Czeb: -57207.9999999999999893
Clen1: -57208.0 BladClen1: -1.06581410364015027881e-14 BladWzgl: 1.86305080345432505766e-19
Clen2: -57208.0 BladClen2: -1.06581410364015027881e-14 BladWzgl: 1.86305080345432505766e-19
x: -14402 Czeb: -57607.9999999999999503
Clen1: -57608.0 BladClen1: -4.9737991503207013011e-14 BladWzgl: 8.63386882085943151193e-19
Clen2: -57608.0 BladClen2: -4.9737991503207013011e-14 BladWzgl: 8.63386882085943151193e-19
x: -14502 Czeb: -58008.0
Clen1: -58008.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -58008.0 BladClen2: 0.0 BladWzgl: 0.0
x: -14602 Czeb: -58407.9999999999999893
Clen1: -58408.0 BladClen1: -1.06581410364015027881e-14 BladWzgl: 1.82477418100285967501e-19
Clen2: -58408.0 BladClen2: -1.06581410364015027881e-14 BladWzgl: 1.82477418100285967501e-19
x: -14702 Czeb: -58808.0000000000000178
Clen1: -58808.0 BladClen1: 1.77635683940025046468e-14 BladWzgl: 3.02060406645396963694e-19
Clen2: -58808.0 BladClen2: 1.77635683940025046468e-14 BladWzgl: 3.020604066453969636

x: -19002 Czeb: -76008.0000000000000426
Clen1: -76008.0 BladClen1: 4.26325641456060111523e-14 BladWzgl: 5.60895749731686284699e-19
Clen2: -76008.0 BladClen2: 4.26325641456060111523e-14 BladWzgl: 5.60895749731686284699e-19
x: -19102 Czeb: -76408.0000000000000355
Clen1: -76408.0 BladClen1: 3.55271367880050092936e-14 BladWzgl: 4.64966191864791766276e-19
Clen2: -76408.0 BladClen2: 3.55271367880050092936e-14 BladWzgl: 4.64966191864791766276e-19
x: -19202 Czeb: -76808.0000000000000213
Clen1: -76808.0 BladClen1: 2.13162820728030055761e-14 BladWzgl: 2.77526847109715206356e-19
Clen2: -76808.0 BladClen2: 2.13162820728030055761e-14 BladWzgl: 2.77526847109715206356e-19
x: -19302 Czeb: -77208.0000000000000071
Clen1: -77208.0 BladClen1: 7.10542735760100185871e-15 BladWzgl: 9.20296777225287775599e-20
Clen2: -77208.0 BladClen2: 7.10542735760100185871e-15 BladWzgl: 9.20296777225287775599e-20
x: -19402 Czeb: -77608.0000000000000284
Clen1: -77608.0 BladClen1: 2.84217094304040074348e-14 BladWzgl: 3.662213

...

Clen1: -320808.0 BladClen1: -1.42108547152020037174e-13 BladWzgl: 4.42970708810316567051e-19
Clen2: -320808.0 BladClen2: -1.42108547152020037174e-13 BladWzgl: 4.42970708810316567051e-19
x: -80302 Czeb: -321207.999999999999829
Clen1: -321208.0 BladClen1: -1.70530256582424044609e-13 BladWzgl: 5.30902893397499578789e-19
Clen2: -321208.0 BladClen2: -1.70530256582424044609e-13 BladWzgl: 5.30902893397499578789e-19
x: -80402 Czeb: -321608.000000000000256
Clen1: -321608.0 BladClen1: 2.55795384873636066914e-13 BladWzgl: 7.95363874261946427676e-19
Clen2: -321608.0 BladClen2: 2.55795384873636066914e-13 BladWzgl: 7.95363874261946427676e-19
x: -80502 Czeb: -322007.999999999999801
Clen1: -322008.0 BladClen1: -1.98951966012828052044e-13 BladWzgl: 6.17847898228702554487e-19
Clen2: -322008.0 BladClen2: -1.98951966012828052044e-13 BladWzgl: 6.17847898228702554487e-19
x: -80602 Czeb: -322408.0
Clen1: -322408.0 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -322408.0 BladClen2: 0.0 BladWzgl: 0.0
x: -80702 Czeb: -322

Clen2: -339208.0 BladClen2: 2.84217094304040074348e-14 BladWzgl: 8.37884408103700603519e-20
x: -84902 Czeb: -339607.999999999999858
Clen1: -339608.0 BladClen1: -1.42108547152020037174e-13 BladWzgl: 4.18448761960907979891e-19
Clen2: -339608.0 BladClen2: -1.42108547152020037174e-13 BladWzgl: 4.18448761960907979891e-19
x: -85002 Czeb: -340007.999999999999972
Clen1: -340008.0 BladClen1: -2.84217094304040074348e-14 BladWzgl: 8.3591296176572337822e-20
Clen2: -340008.0 BladClen2: -2.84217094304040074348e-14 BladWzgl: 8.3591296176572337822e-20
x: -85102 Czeb: -340407.999999999999829
Clen1: -340408.0 BladClen1: -1.70530256582424044609e-13 BladWzgl: 5.00958428069916231963e-19
Clen2: -340408.0 BladClen2: -1.70530256582424044609e-13 BladWzgl: 5.00958428069916231963e-19
x: -85202 Czeb: -340807.999999999999943
Clen1: -340808.0 BladClen1: -5.68434188608080148697e-14 BladWzgl: 1.66790154165418695808e-19
Clen2: -340808.0 BladClen2: -5.68434188608080148697e-14 BladWzgl: 1.66790154165418695808e-19
x: -85

Clen1: -358008.0 BladClen1: -2.84217094304040074348e-14 BladWzgl: 7.93884757614466923554e-20
Clen2: -358008.0 BladClen2: -2.84217094304040074348e-14 BladWzgl: 7.93884757614466923554e-20
x: -89602 Czeb: -358408.000000000000171
Clen1: -358408.0 BladClen1: 1.70530256582424044609e-13 BladWzgl: 4.75799247177585445998e-19
Clen2: -358408.0 BladClen2: 1.70530256582424044609e-13 BladWzgl: 4.75799247177585445998e-19
x: -89702 Czeb: -358807.999999999999773
Clen1: -358808.0 BladClen1: -2.27373675443232059479e-13 BladWzgl: 6.33691766747764987451e-19
Clen2: -358808.0 BladClen2: -2.27373675443232059479e-13 BladWzgl: 6.33691766747764987451e-19
x: -89802 Czeb: -359208.000000000000057
Clen1: -359208.0 BladClen1: 5.68434188608080148697e-14 BladWzgl: 1.58246528086256472191e-19
Clen2: -359208.0 BladClen2: 5.68434188608080148697e-14 BladWzgl: 1.58246528086256472191e-19
x: -89902 Czeb: -359607.999999999999915
Clen1: -359608.0 BladClen1: -8.52651282912120223045e-14 BladWzgl: 2.37105760414707187611e-19
Clen2: 

Clen1: -376408.0 BladClen1: 5.68434188608080148697e-14 BladWzgl: 1.5101543766553318437e-19
Clen2: -376408.0 BladClen2: 5.68434188608080148697e-14 BladWzgl: 1.5101543766553318437e-19
x: -94202 Czeb: -376808.000000000000057
Clen1: -376808.0 BladClen1: 5.68434188608080148697e-14 BladWzgl: 1.50855127441052246395e-19
Clen2: -376808.0 BladClen2: 5.68434188608080148697e-14 BladWzgl: 1.50855127441052246395e-19
x: -94302 Czeb: -377207.999999999999744
Clen1: -377208.0 BladClen1: -2.55795384873636066914e-13 BladWzgl: 6.78128207444264350405e-19
Clen2: -377208.0 BladClen2: -2.55795384873636066914e-13 BladWzgl: 6.78128207444264350405e-19
x: -94402 Czeb: -377607.999999999999687
Clen1: -377608.0 BladClen1: -3.12638803734444081783e-13 BladWzgl: 8.27945392402820072766e-19
Clen2: -377608.0 BladClen2: -3.12638803734444081783e-13 BladWzgl: 8.27945392402820072766e-19
x: -94502 Czeb: -378008.000000000000085
Clen1: -378008.0 BladClen1: 8.52651282912120223045e-14 BladWzgl: 2.25564348614875934601e-19
Clen2: -37

x: -98302 Czeb: -393208.000000000000114
Clen1: -393208.0 BladClen1: 1.13686837721616029739e-13 BladWzgl: 2.89126461622388226344e-19
Clen2: -393208.0 BladClen2: 1.13686837721616029739e-13 BladWzgl: 2.89126461622388226344e-19
x: -98402 Czeb: -393607.999999999999773
Clen1: -393608.0 BladClen1: -2.27373675443232059479e-13 BladWzgl: 5.77665279778947733813e-19
Clen2: -393608.0 BladClen2: -2.27373675443232059479e-13 BladWzgl: 5.77665279778947733813e-19
x: -98502 Czeb: -394008.000000000000313
Clen1: -394008.0 BladClen1: 3.12638803734444081783e-13 BladWzgl: 7.93483390526192568513e-19
Clen2: -394008.0 BladClen2: 3.12638803734444081783e-13 BladWzgl: 7.93483390526192568513e-19
x: -98602 Czeb: -394407.999999999999744
Clen1: -394408.0 BladClen1: -2.55795384873636066914e-13 BladWzgl: 6.48555264785795590057e-19
Clen2: -394408.0 BladClen2: -2.55795384873636066914e-13 BladWzgl: 6.48555264785795590057e-19
x: -98702 Czeb: -394808.000000000000171
Clen1: -394808.0 BladClen1: 1.70530256582424044609e-13 BladW

In [200]:
w20 = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0]
blad(20,w20)

Wyniki dla 20. wielomianu Czebyszwa:
x: -2 Czeb: -1.58631825968e+12
Clen1: -1.58631825968e+12 BladClen1: 0.0 BladWzgl: 0.0
Clen2: -1.58631825968e+12 BladClen2: 0.0 BladWzgl: 0.0
x: -102 Czeb: -1.52691663519261880092e+45
Clen1: -1.52691663519261880077e+45 BladClen1: 1.54742504910672534362e+26 BladWzgl: 1.01343125973050875142e-19
Clen2: -1.52691663519261880092e+45 BladClen2: 0.0 BladWzgl: 0.0
x: -202 Czeb: -6.64091676404337633894e+50
Clen1: -6.64091676404337629269e+50 BladClen1: 4.62438938963258085666e+33 BladWzgl: 6.96348042588171765828e-18
Clen2: -6.64091676404337629391e+50 BladClen2: 4.50269493201067083412e+33 BladWzgl: 6.78023094099009350948e-18
x: -302 Czeb: -1.38264408901219908693e+54
Clen1: -1.38264408901219908875e+54 BladClen1: -1.82768849420425932524e+36 BladWzgl: 1.32187922309783483672e-18
Clen2: -1.38264408901219908842e+54 BladClen2: -1.49538149525803035702e+36 BladWzgl: 1.08153754617095577553e-18
x: -402 Czeb: -3.16871243793242432679e+56
Clen1: -3.16871243793242433402e+56 Bla

Clen1: -1.79911042887747550889e+75 BladClen1: 8.82717431538751982414e+56 BladWzgl: 4.90641050916206726672e-19
Clen2: -1.79911042887747550889e+75 BladClen2: 8.82717431538751982414e+56 BladWzgl: 4.90641050916206726672e-19
x: -4002 Czeb: -2.90980839798968971655e+75
Clen1: -2.90980839798968970263e+75 BladClen1: 1.39273194753891979448e+58 BladWzgl: 4.7863355831302217655e-18
Clen2: -2.90980839798968970224e+75 BladClen2: 1.43196383338508654925e+58 BladWzgl: 4.92116193758459420993e-18
x: -4102 Czeb: -4.65068860725401948645e+75
Clen1: -4.65068860725401944878e+75 BladClen1: 3.7662610412320084583e+58 BladWzgl: 8.09828685446171432208e-18
Clen2: -4.65068860725401944839e+75 BladClen2: 3.80549292707817521308e+58 BladWzgl: 8.18264400919569051272e-18
x: -4202 Czeb: -7.34961713560583166902e+75
Clen1: -7.3496171356058317161e+75 BladClen1: -4.70782630154001057288e+58 BladWzgl: 6.40553951951123329232e-18
Clen2: -7.34961713560583171767e+75 BladClen2: -4.86475384492467759197e+58 BladWzgl: 6.61905750349494106

Clen1: -9.38669820016014552559e+80 BladClen1: -4.62798156746589199356e+62 BladWzgl: 4.93036152732271126194e-19
Clen2: -9.38669820016014552559e+80 BladClen2: -4.62798156746589199356e+62 BladWzgl: 4.93036152732271126194e-19
x: -7902 Czeb: -1.1956480600635090797e+81
Clen1: -1.1956480600635090834e+81 BladClen1: -3.70238525397271359485e+63 BladWzgl: 3.09655104845488938228e-18
Clen2: -1.1956480600635090834e+81 BladClen2: -3.70238525397271359485e+63 BladWzgl: 3.09655104845488938228e-18
x: -8002 Czeb: -1.51835133826265909715e+81
Clen1: -1.51835133826265909386e+81 BladClen1: 3.29100911464241208431e+63 BladWzgl: 2.16748853292945924425e-18
Clen2: -1.51835133826265909396e+81 BladClen2: 3.18816507980983670668e+63 BladWzgl: 2.09975451627541364281e-18
x: -8102 Czeb: -1.92243835067071142655e+81
Clen1: -1.92243835067071143354e+81 BladClen1: -6.99339436861512567916e+63 BladWzgl: 3.63777302204527377749e-18
Clen2: -1.92243835067071143354e+81 BladClen2: -6.99339436861512567916e+63 BladWzgl: 3.6377730220452

Clen1: -2.07750310108494600561e+84 BladClen1: -2.99086908338702410222e+67 BladWzgl: 1.43964602595542983299e-17
Clen2: -2.07750310108494600561e+84 BladClen2: -2.99086908338702410222e+67 BladWzgl: 1.43964602595542983299e-17
x: -11802 Czeb: -2.44206092724960115444e+84
Clen1: -2.44206092724960114665e+84 BladClen1: 7.79310958347323181565e+66 BladWzgl: 3.1912019460752398033e-18
Clen2: -2.44206092724960114644e+84 BladClen2: 8.00373416681034618904e+66 BladWzgl: 3.27745064732051655481e-18
x: -11902 Czeb: -2.86667772693636872575e+84
Clen1: -2.86667772693636876135e+84 BladClen1: -3.55955545839723291039e+67 BladWzgl: 1.24170060169314731694e-17
Clen2: -2.86667772693636876177e+84 BladClen2: -3.60168037506465578507e+67 BladWzgl: 1.25639528336998929701e-17
x: -12002 Czeb: -3.36061472427105242645e+84
Clen1: -3.36061472427105240054e+84 BladClen1: 2.59068237504650679277e+67 BladWzgl: 7.70895383019084138474e-18
Clen2: -3.36061472427105240075e+84 BladClen2: 2.56961991671279535543e+67 BladWzgl: 7.6462794088

Clen1: -3.50291623912058685808e+87 BladClen1: -1.05682990935230507995e+70 BladWzgl: 3.01700022840861318503e-18
Clen2: -3.50291623912058685786e+87 BladClen2: -1.03526195201858456812e+70 BladWzgl: 2.95542879517578434442e-18
x: -17402 Czeb: -3.90826522957814805955e+87
Clen1: -3.90826522957814807033e+87 BladClen1: -1.07839786668602559179e+70 BladWzgl: 2.75927503211553056354e-18
Clen2: -3.90826522957814807011e+87 BladClen2: -1.05682990935230507995e+70 BladWzgl: 2.70408953147321995219e-18
x: -17502 Czeb: -4.3577851790697007345e+87
Clen1: -4.35778517906970071207e+87 BladClen1: 2.24306756270693323092e+70 BladWzgl: 5.14726511412336972137e-18
Clen2: -4.3577851790697007125e+87 BladClen2: 2.19993164803949220724e+70 BladWzgl: 5.04827924654407415e-18
x: -17602 Czeb: -4.85599491660146906694e+87
Clen1: -4.85599491660146902337e+87 BladClen1: 4.35672738141154339082e+70 BladWzgl: 8.97185325815920638002e-18
Clen2: -4.8559949166014690238e+87 BladClen2: 4.31359146674410236715e+70 BladWzgl: 8.883023027880402

...

Clen2: -3.3339014098473972379e+100 BladClen2: -4.09781719453864725897e+83 BladWzgl: 1.2291356854269475263e-17
x: -83502 Czeb: -3.41067696295562703013e+100
Clen1: -3.41067696295562704682e+100 BladClen1: -1.66948107925648592032e+83 BladWzgl: 4.89486719906110879549e-18
Clen2: -3.41067696295562704682e+100 BladClen2: -1.66948107925648592032e+83 BladWzgl: 4.89486719906110879549e-18
x: -83602 Czeb: -3.48912548184027675487e+100
Clen1: -3.48912548184027677081e+100 BladClen1: -1.59359557565391837849e+83 BladWzgl: 4.56732090590621271959e-18
Clen2: -3.489125481840276771e+100 BladClen2: -1.61256695155456026395e+83 BladWzgl: 4.62169377383366763293e-18
x: -83702 Czeb: -3.56928135420743037414e+100
Clen1: -3.56928135420743040184e+100 BladClen1: -2.7698208814937152769e+83 BladWzgl: 7.76016404038499315188e-18
Clen2: -3.56928135420743040184e+100 BladClen2: -2.7698208814937152769e+83 BladWzgl: 7.76016404038499315188e-18
x: -83802 Czeb: -3.65117963221986134419e+100
Clen1: -3.65117963221986133167e+100 BladCl

x: -86602 Czeb: -6.81758289394173090315e+100
Clen1: -6.81758289394173085117e+100 BladClen1: 5.19815699677587661555e+83 BladWzgl: 7.62463336000664499671e-18
Clen2: -6.81758289394173085344e+100 BladClen2: 4.97050048596817399005e+83 BladWzgl: 7.29070781139321528895e-18
x: -86702 Czeb: -6.9687215399788567807e+100
Clen1: -6.96872153997885678905e+100 BladClen1: -8.34740539628242960161e+82 BladWzgl: 1.19783885012397206093e-18
Clen2: -6.96872153997885678829e+100 BladClen2: -7.58855036025675418328e+82 BladWzgl: 1.08894440920361096443e-18
x: -86802 Czeb: -7.12303073217984965818e+100
Clen1: -7.12303073217984960885e+100 BladClen1: 4.93255773416689021913e+83 BladWzgl: 6.92480198335096540496e-18
Clen2: -7.12303073217984960961e+100 BladClen2: 4.8566722305643226773e+83 BladWzgl: 6.81826656822248901432e-18
x: -86902 Czeb: -7.28057321338673563206e+100
Clen1: -7.2805732133867355205e+100 BladClen1: 1.11551690295774286494e+84 BladWzgl: 1.53218279696253896689e-17
Clen2: -7.28057321338673552202e+100 BladClen

Clen2: -1.54163885448768494698e+101 BladClen2: 6.98146633143621384862e+83 BladWzgl: 4.52860039892824572758e-18
x: -90502 Czeb: -1.5743644392155987965e+101
Clen1: -1.57436443921559878375e+101 BladClen1: 1.27487646052313470279e+84 BladWzgl: 8.09772139644059125055e-18
Clen2: -1.57436443921559878375e+101 BladClen2: 1.27487646052313470279e+84 BladWzgl: 8.09772139644059125055e-18
x: -90602 Czeb: -1.60774741992161513221e+101
Clen1: -1.60774741992161512933e+101 BladClen1: 2.88364913689756658965e+83 BladWzgl: 1.79359587281325406508e-18
Clen2: -1.60774741992161512933e+101 BladClen2: 2.88364913689756658965e+83 BladWzgl: 1.79359587281325406508e-18
x: -90702 Czeb: -1.64180025492856549156e+101
Clen1: -1.64180025492856547487e+101 BladClen1: 1.66948107925648592032e+84 BladWzgl: 1.01686004387246536133e-17
Clen2: -1.64180025492856547441e+101 BladClen2: 1.71501238141802644542e+84 BladWzgl: 1.04459259052353259847e-17
x: -90802 Czeb: -1.67653562452208917646e+101
Clen1: -1.67653562452208915961e+101 BladClen

x: -94302 Czeb: -3.43951399221605771349e+101
Clen1: -3.43951399221605774536e+101 BladClen1: -3.18719115130783675698e+84 BladWzgl: 9.26639972542850188604e-18
Clen2: -3.43951399221605774536e+101 BladClen2: -3.18719115130783675698e+84 BladWzgl: 9.26639972542850188604e-18
x: -94402 Czeb: -3.50947881232812420164e+101
Clen1: -3.50947881232812422046e+101 BladClen1: -1.88196048934367503745e+84 BladWzgl: 5.36250705584176697641e-18
Clen2: -3.50947881232812421985e+101 BladClen2: -1.82125208646162100399e+84 BladWzgl: 5.18952295726622610596e-18
x: -94502 Czeb: -3.58079047672040741093e+101
Clen1: -3.58079047672040738937e+101 BladClen1: 2.15514830231291818805e+84 BladWzgl: 6.01863838815497066842e-18
Clen2: -3.58079047672040738937e+101 BladClen2: 2.15514830231291818805e+84 BladWzgl: 6.01863838815497066842e-18
x: -94602 Czeb: -3.65347344604777774292e+101
Clen1: -3.65347344604777771894e+101 BladClen1: 2.39798191384113432192e+84 BladWzgl: 6.56356738115943344517e-18
Clen2: -3.65347344604777771803e+101 Bla

Clen1: -7.2858341298638434275e+101 BladClen1: 8.62059320925167275221e+84 BladWzgl: 1.18319921310269700025e-17
Clen2: -7.28583412986384342629e+101 BladClen2: 8.74201001501578081914e+84 BladWzgl: 1.19986399075203076086e-17
x: -98202 Czeb: -7.42824528984728481846e+101
Clen1: -7.42824528984728472012e+101 BladClen1: 9.83476126689275342153e+84 BladWzgl: 1.32396829710707405578e-17
Clen2: -7.42824528984728472012e+101 BladClen2: 9.83476126689275342153e+84 BladWzgl: 1.32396829710707405578e-17
x: -98302 Czeb: -7.57329085084238233766e+101
Clen1: -7.57329085084238231217e+101 BladClen1: 2.54975292104626940558e+84 BladWzgl: 3.36677010201273154423e-18
Clen2: -7.57329085084238231156e+101 BladClen2: 2.61046132392832343905e+84 BladWzgl: 3.44693129491779658091e-18
x: -98402 Czeb: -7.72101679092896425207e+101
Clen1: -7.72101679092896429942e+101 BladClen1: -4.73525542480021461037e+84 BladWzgl: 6.13294278852421217075e-18
Clen2: -7.72101679092896429942e+101 BladClen2: -4.73525542480021461037e+84 BladWzgl: 6.1

In [201]:
w39 = [0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1]
blad(39,w39)

Wyniki dla 39. wielomianu Czebyszwa:
x: -2 Czeb: 2.27734243043799390028e+23
Clen1: 2.27734243043799390028e+23 BladClen1: 0.0 BladWzgl: 0.0
Clen2: 2.27734243043799390044e+23 BladClen2: 16384.0 BladWzgl: 7.19435065232983794061e-20
x: -102 Czeb: 2.27313292500931272516e+89
Clen1: 2.27313292500931273275e+89 BladClen1: 7.59192098146962016618e+71 BladWzgl: 3.33984911218446104255e-18
Clen2: 2.27313292500931273275e+89 BladClen2: 7.59192098146962016618e+71 BladWzgl: 3.33984911218446104255e-18
x: -202 Czeb: 4.299896762719803295e+100
Clen1: 4.29989676271980325592e+100 BladClen1: -3.90810343553222840439e+83 BladWzgl: 9.088830851511526046e-18
Clen2: 4.29989676271980325554e+100 BladClen2: -3.94604618733351217531e+83 BladWzgl: 9.17707192773979328891e-18
x: -302 Czeb: 1.86390695074638266432e+107
Clen1: 1.86390695074638264809e+107 BladClen1: -1.6232630436415436e+90 BladWzgl: 8.70892746545917622913e-18
Clen2: 1.86390695074638264793e+107 BladClen2: -1.63917738720665677254e+90 BladWzgl: 8.79430910727740344

Clen2: 8.3993598016607566443e+152 BladClen2: -5.81470979436485512439e+135 BladWzgl: 6.92280117969841734683e-18
x: -4902 Czeb: 1.83818804766000152855e+153
Clen1: 1.83818804766000154581e+153 BladClen1: 1.72624197020206636505e+136 BladWzgl: 9.39099768600692615856e-18
Clen2: 1.83818804766000154599e+153 BladClen2: 1.74441293830945653732e+136 BladWzgl: 9.48985029322805169655e-18
x: -5002 Czeb: 3.95971932109031245649e+153
Clen1: 3.9597193210903124256e+153 BladClen1: -3.08906457825632928483e+136 BladWzgl: 7.80122106585512337361e-18
Clen2: 3.95971932109031242523e+153 BladClen2: -3.12540651447110962936e+136 BladWzgl: 7.8930001372181248255e-18
x: -5102 Czeb: 8.40120438410542607969e+153
Clen1: 8.40120438410542588489e+153 BladClen1: -1.94792778111222646667e+137 BladWzgl: 2.31862920130545662012e-17
Clen2: 8.40120438410542588707e+153 BladClen2: -1.92612261938335825996e+137 BladWzgl: 2.29267439681323135941e-17
x: -5202 Czeb: 1.75661874359732340282e+154
Clen1: 1.75661874359732336823e+154 BladClen1: -3.

Clen1: 5.44163476982535779321e+162 BladClen1: -6.36056267126883417144e+145 BladWzgl: 1.16886982318972651349e-17
Clen2: 5.44163476982535779126e+162 BladClen2: -6.5556719556635836859e+145 BladWzgl: 1.20472472574155861507e-17
x: -8802 Czeb: 8.40032775111967771098e+162
Clen1: 8.40032775111967766182e+162 BladClen1: -4.91675396674768776443e+145 BladWzgl: 5.8530501575874045915e-18
Clen2: 8.40032775111967765869e+162 BladClen2: -5.22892882177928698756e+145 BladWzgl: 6.22467238981517631188e-18
x: -8902 Czeb: 1.29042512266009996458e+163
Clen1: 1.29042512266009996607e+163 BladClen1: 1.48283056140009630991e+145 BladWzgl: 1.14910236584930177673e-18
Clen2: 1.29042512266009996583e+163 BladClen2: 1.24869942012639689255e+145 BladWzgl: 9.67665150188885706801e-19
x: -9002 Czeb: 1.97281662724818031635e+163
Clen1: 1.97281662724818035881e+163 BladClen1: 4.24557802842974943468e+146 BladWzgl: 2.15203885135121367352e-17
Clen2: 1.97281662724818035943e+163 BladClen2: 4.30801299943606927931e+146 BladWzgl: 2.183686

x: -12602 Czeb: 7.02917697167430368098e+168
Clen1: 7.02917697167430371003e+168 BladClen1: 2.90513416450782590964e+151 BladWzgl: 4.13296489221246918814e-18
Clen2: 7.02917697167430370921e+168 BladClen2: 2.82329939931042236289e+151 BladWzgl: 4.01654334595296301373e-18
x: -12702 Czeb: 9.49171165918745938027e+168
Clen1: 9.49171165918745957259e+168 BladClen1: 1.92311698213898334863e+152 BladWzgl: 2.02610135156972553188e-17
Clen2: 9.4917116591874595734e+168 BladClen2: 1.93130045865872370331e+152 BladWzgl: 2.03472305944874564057e-17
x: -12802 Czeb: 1.27867945249571513912e+169
Clen1: 1.27867945249571513536e+169 BladClen1: -3.76439919908056315052e+151 BladWzgl: 2.94397410682813617041e-18
Clen2: 1.27867945249571513511e+169 BladClen2: -4.00990349467277379077e+151 BladWzgl: 3.13597241814301461636e-18
x: -12902 Czeb: 1.7185882782454892903e+169
Clen1: 1.71858827824548931502e+169 BladClen1: 2.47140990896158711186e+152 BladWzgl: 1.43804652937855199891e-17
Clen2: 1.71858827824548931469e+169 BladClen2: 2

Clen2: 1.57138685051112231014e+173 BladClen2: -9.78769978885809588269e+155 BladWzgl: 6.22870159927484913801e-18
x: -16502 Czeb: 1.97967807422605908697e+173
Clen1: 1.97967807422605905842e+173 BladClen1: -2.85586308907777318221e+156 BladWzgl: 1.44258964437652436431e-17
Clen2: 1.97967807422605905855e+173 BladClen2: -2.84245528114783058511e+156 BladWzgl: 1.43581692304142331092e-17
x: -16602 Czeb: 2.49057709441106524086e+173
Clen1: 2.49057709441106528913e+173 BladClen1: 4.82681085477933495585e+156 BladWzgl: 1.93802908796152228731e-17
Clen2: 2.49057709441106528967e+173 BladClen2: 4.88044208649910534424e+156 BladWzgl: 1.95956274449442809042e-17
x: -16702 Czeb: 3.12900778086989248339e+173
Clen1: 3.12900778086989242064e+173 BladClen1: -6.2748541112131354426e+156 BladWzgl: 2.0053814341965839429e-17
Clen2: 3.12900778086989242091e+173 BladClen2: -6.2480384953532502484e+156 BladWzgl: 1.99681142806753871228e-17
x: -16802 Czeb: 3.92574134777873439043e+173
Clen1: 3.92574134777873434913e+173 BladClen1:

...

Clen2: 1.48882873829649648205e+200 BladClen2: 3.31961245510479436681e+182 BladWzgl: 2.22968053323786791385e-18
x: -84202 Czeb: 1.55759991134252138916e+200
Clen1: 1.5575999113425213714e+200 BladClen1: -1.77599266348106498624e+183 BladWzgl: 1.1402110712437748118e-17
Clen2: 1.55759991134252137173e+200 BladClen2: -1.74279653893001704258e+183 BladWzgl: 1.11889871477192855361e-17
x: -84302 Czeb: 1.62946038902557973324e+200
Clen1: 1.62946038902557970287e+200 BladClen1: -3.03744539642088684563e+183 BladWzgl: 1.864080536647647323e-17
Clen2: 1.62946038902557970287e+200 BladClen2: -3.03744539642088684563e+183 BladWzgl: 1.864080536647647323e-17
x: -84402 Czeb: 1.70454503376216027053e+200
Clen1: 1.7045450337621602453e+200 BladClen1: -2.52290546587964371878e+183 BladWzgl: 1.48010490536072951249e-17
Clen2: 1.70454503376216024513e+200 BladClen2: -2.53950352815516769061e+183 BladWzgl: 1.48984243763283957496e-17
x: -84502 Czeb: 1.78299442489293763901e+200
Clen1: 1.78299442489293762009e+200 BladClen1: -1

Clen1: 8.33529647492177496519e+200 BladClen1: -1.619970878091139651e+184 BladWzgl: 1.94350720813004160286e-17
Clen2: 8.33529647492177496519e+200 BladClen2: -1.619970878091139651e+184 BladWzgl: 1.94350720813004160286e-17
x: -88102 Czeb: 8.70289219662973646112e+200
Clen1: 8.70289219662973659589e+200 BladClen1: 1.34776265677254651292e+184 BladWzgl: 1.54863765553074208537e-17
Clen2: 8.70289219662973659722e+200 BladClen2: 1.36104110659296569039e+184 BladWzgl: 1.56389516937833560344e-17
x: -88202 Czeb: 9.08625444893209240626e+200
Clen1: 9.08625444893209226152e+200 BladClen1: -1.44735103042569034393e+184 BladWzgl: 1.59290171605946774668e-17
Clen2: 9.08625444893209226019e+200 BladClen2: -1.4606294802461095214e+184 BladWzgl: 1.60751549327102249663e-17
x: -88302 Czeb: 9.48604043756764573793e+200
Clen1: 9.48604043756764574723e+200 BladClen1: 9.29491487429342422707e+182 BladWzgl: 9.79851913500462707771e-19
Clen2: 9.48604043756764574856e+200 BladClen2: 1.06227598563353419738e+183 BladWzgl: 1.119830

Clen2: 4.15514199962410807362e+201 BladClen2: 1.43407258060527116646e+184 BladWzgl: 3.45132026952388995104e-18
x: -91902 Czeb: 4.33064940326545287066e+201
Clen1: 4.33064940326545291793e+201 BladClen1: 4.72712813606922717834e+184 BladWzgl: 1.0915517964822588111e-17
Clen2: 4.33064940326545291873e+201 BladClen2: 4.80679883499174224314e+184 BladWzgl: 1.10994873687240924054e-17
x: -92002 Czeb: 4.51336692555625782854e+201
Clen1: 4.51336692555625776932e+201 BladClen1: -5.92218861990695315039e+184 BladWzgl: 1.31214428553846475032e-17
Clen2: 4.51336692555625776879e+201 BladClen2: -5.97530241918862986026e+184 BladWzgl: 1.3239123957226662279e-17
x: -92102 Czeb: 4.70358244547893831773e+201
Clen1: 4.70358244547893825346e+201 BladClen1: -6.42676971308288189414e+184 BladWzgl: 1.3663563438247506865e-17
Clen2: 4.70358244547893825399e+201 BladClen2: -6.37365591380120518428e+184 BladWzgl: 1.35506414263611638329e-17
x: -92202 Czeb: 4.90159500456492858736e+201
Clen1: 4.90159500456492866385e+201 BladClen1: 

Clen1: 2.01930986983678373585e+202 BladClen1: 2.76191756264718891319e+184 BladWzgl: 1.36775321306701110057e-18
Clen2: 2.01930986983678373564e+202 BladClen2: 2.54946236552048207371e+184 BladWzgl: 1.26254142744647178513e-18
x: -95802 Czeb: 2.10105933583935925408e+202
Clen1: 2.10105933583935928552e+202 BladClen1: 3.14433691747526122424e+185 BladWzgl: 1.49654836674049450559e-17
Clen2: 2.10105933583935928446e+202 BladClen2: 3.0381093189119078045e+185 BladWzgl: 1.44598930029655888037e-17
x: -95902 Czeb: 2.18602782551775674502e+202
Clen1: 2.186027825517756755e+202 BladClen1: 9.98539426495522145536e+184 BladWzgl: 4.56782578354884336666e-18
Clen2: 2.18602782551775675479e+202 BladClen2: 9.77293906782851461589e+184 BladWzgl: 4.47063800092014457164e-18
x: -96002 Czeb: 2.27433853692469474431e+202
Clen1: 2.27433853692469471776e+202 BladClen1: -2.65568996408383549345e+185 BladWzgl: 1.16767575317735893189e-17
Clen2: 2.27433853692469471776e+202 BladClen2: -2.65568996408383549345e+185 BladWzgl: 1.167675

Clen2: 8.86774567752107329078e+202 BladClen2: 1.98008243722090774391e+186 BladWzgl: 2.23290395239935242794e-17
x: -99602 Czeb: 9.21277973694949179183e+202
Clen1: 9.21277973694949196094e+202 BladClen1: 1.69114336912858644223e+186 BladWzgl: 1.8356494102924822574e-17
Clen2: 9.21277973694949195924e+202 BladClen2: 1.67414695335844989507e+186 BladWzgl: 1.81720067250059801359e-17
x: -99702 Czeb: 9.57087207274648289698e+202
Clen1: 9.57087207274648290972e+202 BladClen1: 1.27473118276024103686e+185 BladWzgl: 1.33188613646827356184e-18
Clen2: 9.57087207274648290802e+202 BladClen2: 1.10476702505887556527e+185 BladWzgl: 1.15430131827250375362e-18
x: -99802 Czeb: 9.94250304619120434224e+202
Clen1: 9.94250304619120450116e+202 BladClen1: 1.58916487450776715928e+186 BladWzgl: 1.59835492845692201263e-17
Clen2: 9.94250304619120450116e+202 BladClen2: 1.58916487450776715928e+186 BladWzgl: 1.59835492845692201263e-17
x: -99902 Czeb: 1.03281701807879170583e+203
Clen1: 1.03281701807879171093e+203 BladClen1: 5.

## Dowolny wielomian
Obliczanie pochodnej dla wielomianu: 
$$W(x) = x^5 + 4x^4 + - x^3 - 3/2$$
jest on kombinacją liniową wielomianów Czebyszewa:
$$W(x) = \frac{T_5}{16} + \frac{T_4}{2} + \frac{T_3}{16} + T_2 - \frac{T_1}{8}$$
wzór na jego pochodną to:
$$W'(x) = 5x^4 + 16x^3 - 3x^2$$
która będzie obliczana przez funkcję wiel(x).

In [205]:
function wiel(x)
    return ((BigFloat(x) * BigFloat(5) + BigFloat(16)) * BigFloat(x) - BigFloat(3)) * BigFloat(x) * BigFloat(x)
end

wiel (generic function with 1 method)

In [216]:
ww = [0,1/8,1,1/16,1/2,1/16]
start = -100050
iter = 100
finish = 100050
function blad2(w)
    licz = 0
    sum1 = 0
    sum2 = 0
    print("Wyniki dla pochodnej wielomianu:")
    for i in start:iter:finish
        wynclen1 = Clen1(a,b,c,w,i)
        wynclen2 = Clen2(a,b,c,w,i)
        wyn = wiel(i)
        print("x: ")
        print(i)
        print(" wiel:")
        println(wyn)
        print("Clen1: ")
        print(wynclen1)
        print(" BladClen1: ")
        print(wynclen1 - wyn)
        if(wyn != 0)
            licz += 1
            sum1 += abs((wynclen1 - wyn)/wyn)
            print(" BladWzgl: ")
            print(abs((wynclen1 - wyn)/wyn))
        end
        println()
        print("Clen2: ")
        print(wynclen2)
        print(" BladClen2: ")
        print(wynclen2 - wyn)
        if(wyn != 0)
            sum2 += abs((wynclen2 - wyn)/wyn)
            print(" BladWzgl: ")
            print(abs((wynclen2 - wyn)/wyn))
        end
        println()
    end
    print("Sredni błąd względny dla Clen1 wynosił: ")
    println(sum1/licz)
    print("Sredni błąd względny dla Clen2 wynosił: ")
    print(sum2/licz)
end

blad2 (generic function with 1 method)

In [217]:
blad2(ww)

Wyniki dla pochodnej wielomianu:x: -100050 wiel:5.00984726207999242496e+20
Clen1: 5.00984726207999642688e+20 BladClen1: 400192.0 BladWzgl: 7.98810780179050733802e-16
Clen2: 5.0098472620799964272e+20 BladClen2: 400224.0 BladWzgl: 7.98874654381847715342e-16
x: -99950 wiel:4.98984773708063242496e+20
Clen1: 4.98984773708063642272e+20 BladClen1: 399776.0 BladWzgl: 8.01178755474197150657e-16
Clen2: 4.98984773708063642336e+20 BladClen2: 399840.0 BladWzgl: 8.01307015900911982527e-16
x: -99850 wiel:4.96990815114675182496e+20
Clen1: 4.96990815114675581952e+20 BladClen1: 399456.0 BladWzgl: 8.03749260251077088639e-16
Clen2: 4.9699081511467558192e+20 BladClen2: 399424.0 BladWzgl: 8.03684872743246352667e-16
x: -99750 wiel:4.95002838439931062496e+20
Clen1: 4.95002838439931461536e+20 BladClen1: 399040.0 BladWzgl: 8.06136791574022015546e-16
Clen2: 4.95002838439931461504e+20 BladClen2: 399008.0 BladWzgl: 8.06072145480070610402e-16
x: -99650 wiel:4.93020831707926882496e+20
Clen1: 4.93020831707927281088e+

Clen2: 4.13274128205970763904e+20 BladClen2: 381408.0 BladWzgl: 9.22893483934497046741e-16
x: -95250 wiel:4.11543124969563562496e+20
Clen1: 4.11543124969563943488e+20 BladClen1: 380992.0 BladWzgl: 9.25764462784251279184e-16
Clen2: 4.1154312496956394352e+20 BladClen2: 381024.0 BladWzgl: 9.25842218912487819695e-16
x: -95150 wiel:4.09817565180216682496e+20
Clen1: 4.09817565180217063072e+20 BladClen1: 380576.0 BladWzgl: 9.28647360033585318783e-16
Clen2: 4.09817565180217063136e+20 BladClen2: 380640.0 BladWzgl: 9.28803527083115897365e-16
x: -95050 wiel:4.08097437414025742496e+20
Clen1: 4.08097437414026122752e+20 BladClen1: 380256.0 BladWzgl: 9.31777475520435917062e-16
Clen2: 4.0809743741402612272e+20 BladClen2: 380224.0 BladWzgl: 9.31699062874174835113e-16
x: -94950 wiel:4.06382730259086742496e+20
Clen1: 4.06382730259087122336e+20 BladClen1: 379840.0 BladWzgl: 9.34685388224631020874e-16
Clen2: 4.06382730259087122304e+20 BladClen2: 379808.0 BladWzgl: 9.346066447209895187e-16
x: -94850 wiel:4.

Clen2: 3.39110490395574925504e+20 BladClen2: 363008.0 BladWzgl: 1.07047115993536159631e-15
x: -90650 wiel:3.37618244143284982496e+20
Clen1: 3.37618244143285345088e+20 BladClen1: 362592.0 BladWzgl: 1.07397039789744351121e-15
Clen2: 3.3761824414328534512e+20 BladClen2: 362624.0 BladWzgl: 1.07406517950523606641e-15
x: -90550 wiel:3.36130928258471342496e+20
Clen1: 3.36130928258471704704e+20 BladClen1: 362208.0 BladWzgl: 1.07758010212459956781e-15
Clen2: 3.36130928258471704704e+20 BladClen2: 362208.0 BladWzgl: 1.07758010212459956781e-15
x: -90450 wiel:3.34648531869229642496e+20
Clen1: 3.34648531869230004288e+20 BladClen1: 361792.0 BladWzgl: 1.08111037565040682842e-15
Clen2: 3.34648531869230004288e+20 BladClen2: 361792.0 BladWzgl: 1.08111037565040682842e-15
x: -90350 wiel:3.33171044115655882496e+20
Clen1: 3.33171044115656243872e+20 BladClen1: 361376.0 BladWzgl: 1.08465608396194581482e-15
Clen2: 3.33171044115656243904e+20 BladClen2: 361408.0 BladWzgl: 1.08475213072400744116e-15
x: -90250 wiel

Clen2: 2.75407015845132127104e+20 BladClen2: 344608.0 BladWzgl: 1.25126805118785228295e-15
x: -86050 wiel:2.74130496236095442496e+20
Clen1: 2.7413049623609578672e+20 BladClen1: 344224.0 BladWzgl: 1.25569392944715055014e-15
Clen2: 2.74130496236095786704e+20 BladClen2: 344208.0 BladWzgl: 1.25563556308434274358e-15
x: -85950 wiel:2.72858419306951042496e+20
Clen1: 2.7285841930695138632e+20 BladClen1: 343824.0 BladWzgl: 1.26008206334002286013e-15
Clen2: 2.72858419306951386304e+20 BladClen2: 343808.0 BladWzgl: 1.26002342487088329923e-15
x: -85850 wiel:2.71590774737794582496e+20
Clen1: 2.71590774737794925904e+20 BladClen1: 343408.0 BladWzgl: 1.2644317552079626279e-15
Clen2: 2.71590774737794925904e+20 BladClen2: 343408.0 BladWzgl: 1.2644317552079626279e-15
x: -85750 wiel:2.70327552220722062496e+20
Clen1: 2.70327552220722405504e+20 BladClen1: 343008.0 BladWzgl: 1.26886067358733176818e-15
Clen2: 2.70327552220722405504e+20 BladClen2: 343008.0 BladWzgl: 1.26886067358733176818e-15
x: -85650 wiel:2.

Clen2: 2.21130589594898368704e+20 BladClen2: 326208.0 BladWzgl: 1.47518260860064345878e-15
x: -81450 wiel:2.20047934320250942496e+20
Clen1: 2.20047934320251268304e+20 BladClen1: 325808.0 BladWzgl: 1.48062285159118620169e-15
Clen2: 2.20047934320251268304e+20 BladClen2: 325808.0 BladWzgl: 1.48062285159118620169e-15
x: -81350 wiel:2.18969259429911782496e+20
Clen1: 2.18969259429912107904e+20 BladClen1: 325408.0 BladWzgl: 1.486089877854098468e-15
Clen2: 2.18969259429912107904e+20 BladClen2: 325408.0 BladWzgl: 1.486089877854098468e-15
x: -81250 wiel:2.17894555155976562496e+20
Clen1: 2.1789455515597688752e+20 BladClen1: 325024.0 BladWzgl: 1.491657282428817116e-15
Clen2: 2.17894555155976887504e+20 BladClen2: 325008.0 BladWzgl: 1.49158385241589849743e-15
x: -81150 wiel:2.16823811742541282496e+20
Clen1: 2.1682381174254160712e+20 BladClen1: 324624.0 BladWzgl: 1.49717873415795178792e-15
Clen2: 2.16823811742541607104e+20 BladClen2: 324608.0 BladWzgl: 1.49710494152479303437e-15
x: -81050 wiel:2.1575

...

Clen1: 1.78990195748227873088e+20 BladClen1: -309408.0 BladWzgl: 1.72863099404182208487e-15
Clen2: 1.78990195748227873104e+20 BladClen2: -309392.0 BladWzgl: 1.72854160367084050336e-15
x: 77450 wiel:1.79917594538833742496e+20
Clen1: 1.79917594538833432688e+20 BladClen1: -309808.0 BladWzgl: 1.72194387543976681478e-15
Clen2: 1.79917594538833432704e+20 BladClen2: -309792.0 BladWzgl: 1.72185494583818442737e-15
x: 77550 wiel:1.80848592506291242496e+20
Clen1: 1.80848592506290932304e+20 BladClen1: -310192.0 BladWzgl: 1.71520273230331744868e-15
Clen2: 1.80848592506290932304e+20 BladClen2: -310192.0 BladWzgl: 1.71520273230331744868e-15
x: 77650 wiel:1.81783198950696682496e+20
Clen1: 1.81783198950696371904e+20 BladClen1: -310592.0 BladWzgl: 1.70858474156480707551e-15
Clen2: 1.81783198950696371904e+20 BladClen2: -310592.0 BladWzgl: 1.70858474156480707551e-15
x: 77750 wiel:1.82721423184146062496e+20
Clen1: 1.82721423184145751488e+20 BladClen1: -311008.0 BladWzgl: 1.70208831882054212151e-15
Clen2: 1

Clen1: 2.2551882183512151472e+20 BladClen1: -327776.0 BladWzgl: 1.45343079275058908908e-15
Clen2: 2.25518821835121514704e+20 BladClen2: -327792.0 BladWzgl: 1.45350174026561157218e-15
x: 82050 wiel:2.26621590520276642496e+20
Clen1: 2.2662159052027631432e+20 BladClen1: -328176.0 BladWzgl: 1.44812327566219654629e-15
Clen2: 2.26621590520276314304e+20 BladClen2: -328192.0 BladWzgl: 1.44819387793783704144e-15
x: 82150 wiel:2.27728398606699382496e+20
Clen1: 2.27728398606699053904e+20 BladClen1: -328592.0 BladWzgl: 1.44291182834644225944e-15
Clen2: 2.27728398606699053904e+20 BladClen2: -328592.0 BladWzgl: 1.44291182834644225944e-15
x: 82250 wiel:2.28839255946486062496e+20
Clen1: 2.28839255946485733504e+20 BladClen1: -328992.0 BladWzgl: 1.43765543476917528127e-15
Clen2: 2.28839255946485733504e+20 BladClen2: -328992.0 BladWzgl: 1.43765543476917528127e-15
x: 82350 wiel:2.29954172403732682496e+20
Clen1: 2.2995417240373235312e+20 BladClen1: -329376.0 BladWzgl: 1.43235496254319529667e-15
Clen2: 2.29

x: 86550 wiel:2.80578474701840542496e+20
Clen1: 2.80578474701840196304e+20 BladClen1: -346192.0 BladWzgl: 1.23385088741352775277e-15
Clen2: 2.80578474701840196304e+20 BladClen2: -346192.0 BladWzgl: 1.23385088741352775277e-15
x: 86650 wiel:2.81877434924680582496e+20
Clen1: 2.81877434924680235904e+20 BladClen1: -346592.0 BladWzgl: 1.22958405695940703786e-15
Clen2: 2.81877434924680235904e+20 BladClen2: -346592.0 BladWzgl: 1.22958405695940703786e-15
x: 86750 wiel:2.83180900165204562496e+20
Clen1: 2.8318090016520421552e+20 BladClen1: -346976.0 BladWzgl: 1.22528037659876810705e-15
Clen2: 2.83180900165204215504e+20 BladClen2: -346992.0 BladWzgl: 1.22533687758450078108e-15
x: 86850 wiel:2.84488880827508482496e+20
Clen1: 2.8448888082750813512e+20 BladClen1: -347376.0 BladWzgl: 1.22105299507512662354e-15
Clen2: 2.84488880827508135104e+20 BladClen2: -347392.0 BladWzgl: 1.2211092362890308715e-15
x: 86950 wiel:2.85801387327688342496e+20
Clen1: 2.85801387327687994704e+20 BladClen1: -347792.0 BladWzg

Clen2: 3.43641074298982578304e+20 BladClen2: -364192.0 BladWzgl: 1.0598034613380845232e-15
x: 91150 wiel:3.45153230652640282496e+20
Clen1: 3.45153230652639917888e+20 BladClen1: -364608.0 BladWzgl: 1.05636560118696630946e-15
Clen2: 3.45153230652639917888e+20 BladClen2: -364608.0 BladWzgl: 1.05636560118696630946e-15
x: 91250 wiel:3.46670372088301562496e+20
Clen1: 3.46670372088301197472e+20 BladClen1: -365024.0 BladWzgl: 1.05294259154925279838e-15
Clen2: 3.46670372088301197504e+20 BladClen2: -364992.0 BladWzgl: 1.05285028484358529139e-15
x: 91350 wiel:3.48192509550062782496e+20
Clen1: 3.4819250955006241712e+20 BladClen1: -365376.0 BladWzgl: 1.04935054597280643647e-15
Clen2: 3.4819250955006241712e+20 BladClen2: -365376.0 BladWzgl: 1.04935054597280643647e-15
x: 91450 wiel:3.49719653994019942496e+20
Clen1: 3.49719653994019576704e+20 BladClen1: -365792.0 BladWzgl: 1.0459578002620776006e-15
Clen2: 3.49719653994019576704e+20 BladClen2: -365792.0 BladWzgl: 1.0459578002620776006e-15
x: 91550 wiel

Clen1: 4.18527916038578099904e+20 BladClen1: -382592.0 BladWzgl: 9.14137349836262698048e-16
Clen2: 4.18527916038578099904e+20 BladClen2: -382592.0 BladWzgl: 9.14137349836262698048e-16
x: 95750 wiel:4.20280895463777062496e+20
Clen1: 4.2028089546377667952e+20 BladClen1: -382976.0 BladWzgl: 9.11238184113481132065e-16
Clen2: 4.2028089546377667952e+20 BladClen2: -382976.0 BladWzgl: 9.11238184113481132065e-16
x: 95850 wiel:4.22039375819395582496e+20
Clen1: 4.22039375819395199136e+20 BladClen1: -383360.0 BladWzgl: 9.08351262854801137646e-16
Clen2: 4.22039375819395199104e+20 BladClen2: -383392.0 BladWzgl: 9.08427085163887515029e-16
x: 95950 wiel:4.23803368601530042496e+20
Clen1: 4.23803368601529658688e+20 BladClen1: -383808.0 BladWzgl: 9.05627534926144877725e-16
Clen2: 4.2380336860152965872e+20 BladClen2: -383776.0 BladWzgl: 9.05552028211543731759e-16
x: 96050 wiel:4.25572885318276442496e+20
Clen1: 4.25572885318276058272e+20 BladClen1: -384224.0 BladWzgl: 9.02839474165858720069e-16
Clen2: 4.25

In [220]:
start = -10
iter = 0.01
finish = 10
blad2(ww)

Wyniki dla pochodnej wielomianu:x: -10.0 wiel:33700.0
Clen1: 33740.25 BladClen1: 40.25 BladWzgl: 0.00119436201780415430267
Clen2: 33740.25 BladClen2: 40.25 BladWzgl: 0.00119436201780415430267
x: -9.99 wiel:33548.851516050003216
Clen1: 33589.0615160500032168 BladClen1: 40.2100000000000008527 BladWzgl: 0.0011985507158348850782
Clen2: 33589.0615160500032168 BladClen2: 40.2100000000000008527 BladWzgl: 0.0011985507158348850782
x: -9.98 wiel:33398.2053288000064128
Clen1: 33438.3753288000064146 BladClen1: 40.1700000000000017053 BladWzgl: 0.00120275923824447321213
Clen2: 33438.3753288000064146 BladClen2: 40.1700000000000017053 BladWzgl: 0.00120275923824447321213
x: -9.97 wiel:33248.0603360500095853
Clen1: 33288.1903360500095914 BladClen1: 40.1300000000000061107 BladWzgl: 0.00120698770377555191754
Clen2: 33288.1903360500095914 BladClen2: 40.1300000000000061107 BladWzgl: 0.00120698770377555191754
x: -9.96 wiel:33098.4154368000127349
Clen1: 33138.5054368000127418 BladClen1: 40.0900000000000069633

Clen2: 27679.2649520500037177 BladClen2: 38.5300000000000011369 BladWzgl: 0.00139395714574305788517
x: -9.56 wiel:27510.204748800006481
Clen1: 27548.6947488000064865 BladClen1: 38.4900000000000055422 BladWzgl: 0.00139911717675161749154
Clen2: 27548.6947488000064812 BladClen2: 38.4900000000000002132 BladWzgl: 0.00139911717675161729789
x: -9.55 wiel:27380.1305312500092253
Clen1: 27418.5805312500092263 BladClen1: 38.4500000000000010658 BladWzgl: 0.00140430302025461561358
Clen2: 27418.5805312500092299 BladClen2: 38.4500000000000046185 BladWzgl: 0.00140430302025461574339
x: -9.54 wiel:27250.5112487999889659
Clen1: 27288.9212487999889678 BladClen1: 38.4100000000000019185 BladWzgl: 0.00140951483989833164241
Clen2: 27288.9212487999889643 BladClen2: 38.4099999999999983658 BladWzgl: 0.00140951483989833151208
x: -9.53 wiel:27121.3458520499917537
Clen1: 27159.7158520499917493 BladClen1: 38.3699999999999956657 BladWzgl: 0.00141475280059155928983
Clen2: 27159.7158520499917529 BladClen2: 38.369999999

Clen2: 22351.7872360500087314 BladClen2: 36.7700000000000049027 BladWzgl: 0.0016477692851878199669
x: -9.12 wiel:22203.5724287999913056
Clen1: 22240.3024287999913025 BladClen1: 36.7299999999999968736 BladWzgl: 0.001654238304118933046
Clen2: 22240.3024287999913042 BladClen2: 36.72999999999999865 BladWzgl: 0.00165423830411893312604
x: -9.11 wiel:22092.5385160499937012
Clen1: 22129.2285160499936971 BladClen1: 36.6899999999999959499 BladWzgl: 0.00166074170124655897308
Clen2: 22129.2285160499936971 BladClen2: 36.6899999999999959499 BladWzgl: 0.00166074170124655897308
x: -9.1 wiel:21981.9144999999960781
Clen1: 22018.5644999999960767 BladClen1: 36.6499999999999985789 BladWzgl: 0.00166727970850764637078
Clen2: 22018.5644999999960749 BladClen2: 36.6499999999999968026 BladWzgl: 0.00166727970850764628989
x: -9.09 wiel:21871.6993840499984376
Clen1: 21908.3093840499984353 BladClen1: 36.6099999999999976552 BladWzgl: 0.00167385255974658963169
Clen2: 21908.309384049998437 BladClen2: 36.609999999999999

Clen2: 17822.1099520499952984 BladClen2: 35.0099999999999980105 BladWzgl: 0.00196828038828021722926
x: -8.68 wiel:17692.8064767999973252
Clen1: 17727.7764767999973223 BladClen1: 34.9699999999999970868 BladWzgl: 0.00197650949530562167529
Clen2: 17727.7764767999973223 BladClen2: 34.9699999999999970868 BladWzgl: 0.00197650949530562167529
x: -8.67 wiel:17598.881128049999333
Clen1: 17633.8111280499993327 BladClen1: 34.9299999999999997158 BladWzgl: 0.00198478526821382833631
Clen2: 17633.8111280499993327 BladClen2: 34.9299999999999997158 BladWzgl: 0.00198478526821382833631
x: -8.66 wiel:17505.3229608000013275
Clen1: 17540.2129608000013263 BladClen1: 34.8899999999999987921 BladWzgl: 0.00199310804365791087992
Clen2: 17540.2129608000013281 BladClen2: 34.8900000000000005684 BladWzgl: 0.00199310804365791098135
x: -8.65 wiel:17412.1310312500033035
Clen1: 17446.9810312500033049 BladClen1: 34.8500000000000014211 BladWzgl: 0.00200147816125744759611
Clen2: 17446.9810312500033067 BladClen2: 34.850000000

Clen2: 14007.33203125 BladClen2: 33.25 BladWzgl: 0.00237940495308697882379
x: -8.24 wiel:13895.1080448000016796
Clen1: 13928.3180448000016796 BladClen1: 33.2099999999999999645 BladWzgl: 0.00239004978535796667182
Clen2: 13928.3180448000016813 BladClen2: 33.2100000000000017408 BladWzgl: 0.00239004978535796679972
x: -8.23 wiel:13816.4617400500033462
Clen1: 13849.631740050003347 BladClen1: 33.1700000000000008171 BladWzgl: 0.00240075937125418875984
Clen2: 13849.6317400500033479 BladClen2: 33.1700000000000017053 BladWzgl: 0.00240075937125418882421
x: -8.22 wiel:13738.1422248000049988
Clen1: 13771.2722248000049996 BladClen1: 33.1300000000000007816 BladWzgl: 0.00241153421313355893497
Clen2: 13771.2722248000050023 BladClen2: 33.1300000000000034461 BladWzgl: 0.00241153421313355912894
x: -8.21 wiel:13660.1486080500066365
Clen1: 13693.2386080500066416 BladClen1: 33.090000000000005187 BladWzgl: 0.00242237481812605404788
Clen2: 13693.2386080500066399 BladClen2: 33.0900000000000034106 BladWzgl: 0.002

...

Clen1: 27660.8956488000050733 BladClen1: -31.5100000000000033396 BladWzgl: 0.00113785708614901161776
Clen2: 27660.8956488000050733 BladClen2: -31.5100000000000033396 BladWzgl: 0.00113785708614901161776
x: 7.95 wiel:27822.5305312500023156
Clen1: 27790.9805312500023149 BladClen1: -31.5500000000000007105 BladWzgl: 0.00113397305700009350524
Clen2: 27790.9805312500023149 BladClen2: -31.5500000000000007105 BladWzgl: 0.00113397305700009350524
x: 7.96 wiel:27953.1103487999995352
Clen1: 27921.5203487999995353 BladClen1: -31.5899999999999998579 BladWzgl: 0.00113010679691164058741
Clen2: 27921.5203487999995371 BladClen2: -31.5899999999999980815 BladWzgl: 0.00113010679691164052388
x: 7.97 wiel:28084.1461520499967364
Clen1: 28052.5161520499967374 BladClen1: -31.6299999999999990052 BladWzgl: 0.00112625820378345999179
Clen2: 28052.5161520499967356 BladClen2: -31.6300000000000007816 BladWzgl: 0.0011262582037834600551
x: 7.98 wiel:28215.6389928000056155
Clen1: 28183.9689928000056156 BladClen1: -31.6699

x: 8.38 wiel:33862.3461288000117939
Clen1: 33829.0761288000117943 BladClen1: -33.2699999999999995737 BladWzgl: 0.000982507233062146856764
Clen2: 33829.0761288000117943 BladClen2: -33.2699999999999995737 BladWzgl: 0.000982507233062146856764
x: 8.39 wiel:34013.4979160500086053
Clen1: 33980.187916050008603 BladClen1: -33.3100000000000022737 BladWzgl: 0.000979317095883924201094
Clen2: 33980.187916050008603 BladClen2: -33.3100000000000022737 BladWzgl: 0.000979317095883924201094
x: 8.4 wiel:34165.1520000000053976
Clen1: 34131.8020000000053926 BladClen1: -33.3500000000000049738 BladWzgl: 0.00097614083496540567724
Clen2: 34131.8020000000053926 BladClen2: -33.3500000000000049738 BladWzgl: 0.00097614083496540567724
x: 8.41 wiel:34317.3094840500021654
Clen1: 34283.9194840500021648 BladClen1: -33.3900000000000005684 BladWzgl: 0.000972978374529011475567
Clen2: 34283.9194840500021648 BladClen2: -33.3900000000000005684 BladWzgl: 0.000972978374529011475567
x: 8.42 wiel:34469.9714727999989137
Clen1: 34

Clen2: 41492.4185312499937588 BladClen2: -35.1500000000000021316 BladWzgl: 0.000846425669577769891293
x: 8.86 wiel:41703.540496799989981
Clen1: 41668.3504967999899833 BladClen1: -35.1899999999999977263 BladWzgl: 0.000843813248966240853749
Clen2: 41668.3504967999899833 BladClen2: -35.1899999999999977263 BladWzgl: 0.000843813248966240853749
x: 8.87 wiel:41880.0679160499861808
Clen1: 41844.837916049986184 BladClen1: -35.2299999999999968736 BladWzgl: 0.000841211625315883547375
Clen2: 41844.837916049986184 BladClen2: -35.2299999999999968736 BladWzgl: 0.000841211625315883547375
x: 8.88 wiel:42057.1519488000138622
Clen1: 42021.8819488000138591 BladClen1: -35.2700000000000031264 BladWzgl: 0.000838620742625115783489
Clen2: 42021.8819488000138591 BladClen2: -35.2700000000000031264 BladWzgl: 0.000838620742625115783489
x: 8.89 wiel:42234.7937560500101135
Clen1: 42199.4837560500101112 BladClen1: -35.3100000000000022737 BladWzgl: 0.000836040545242202077017
Clen2: 42199.4837560500101112 BladClen2: -3

Clen1: 49774.4075080499828445 BladClen1: -36.9100000000000001421 BladWzgl: 0.000740996260418829374647
Clen2: 49774.4075080499828481 BladClen2: -36.9099999999999965894 BladWzgl: 0.000740996260418829303284
x: 9.3 wiel:50012.8425000000143399
Clen1: 49975.892500000014337 BladClen1: -36.9500000000000028422 BladWzgl: 0.000738810236590731515555
Clen2: 49975.892500000014337 BladClen2: -36.9500000000000028422 BladWzgl: 0.000738810236590731515555
x: 9.31 wiel:50214.9751120500100683
Clen1: 50177.9851120500100663 BladClen1: -36.9900000000000019895 BladWzgl: 0.000736632845430278203728
Clen2: 50177.9851120500100699 BladClen2: -36.9899999999999984368 BladWzgl: 0.000736632845430278132948
x: 9.32 wiel:50417.7165568000057689
Clen1: 50380.6865568000057749 BladClen1: -37.0299999999999940314 BladWzgl: 0.000734464044167538450187
Clen2: 50380.6865568000057678 BladClen2: -37.0300000000000011369 BladWzgl: 0.000734464044167538591165
x: 9.33 wiel:50621.0680480500014475
Clen1: 50583.9980480500014437 BladClen1: -3

Clen2: 59002.0559008000146051 BladClen2: -38.6299999999999990052 BladWzgl: 0.000654294566714655220444
x: 9.73 wiel:59269.4483440500097657
Clen1: 59230.7783440500097676 BladClen1: -38.6699999999999981526 BladWzgl: 0.000652444068241138505332
Clen2: 59230.778344050009764 BladClen2: -38.6700000000000017053 BladWzgl: 0.00065244406824113856526
x: 9.74 wiel:59498.8716328000048996
Clen1: 59460.1616328000048988 BladClen1: -38.7100000000000008527 BladWzgl: 0.000650600573383988325237
Clen2: 59460.1616328000048952 BladClen2: -38.7100000000000044054 BladWzgl: 0.000650600573383988384953
x: 9.75 wiel:59728.95703125
Clen1: 59690.20703125 BladClen1: -38.75 BladWzgl: 0.000648764048897189406351
Clen2: 59690.20703125 BladClen2: -38.75 BladWzgl: 0.000648764048897189406351
x: 9.76 wiel:59959.7058047999950752
Clen1: 59920.915804799995076 BladClen1: -38.7899999999999991473 BladWzgl: 0.000646934461724705742572
Clen2: 59920.9158047999950725 BladClen2: -38.7900000000000027001 BladWzgl: 0.000646934461724705801865